In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
from os import listdir
import re

import csv
import datetime
import pickle

In [2]:
pd.set_option('display.max_rows', 800)
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_colwidth', 100)
pd.options.display.float_format = '{:.0f}'.format

In [3]:
# Functions shared across multiple notebooks are stored in yahoo_data_ext_kit.py which can be found in the same
# directory as the notebooks.

import yahoo_data_ext_kit as ext

In [4]:
%load_ext autoreload
%autoreload 2

In [5]:
master_company_data = pd.read_pickle('/home/priyesh/projects/TS1/pickle/yahoo_company_data.pkl')
drop_data_details = pd.read_pickle('/home/priyesh/projects/TS1/pickle/yahoo_drop_data_details_stage4.pkl')

## Cash Sheet

Extract Cash sheet from data downloaded from Yahoo and format as a dataframe.

In [6]:
cash_sheets = ext.extract_statements('cash',master_company_data)

AM
AR
APA
BKR
LNG
CHK
CVX
COP
CTRA
DVN
FANG
DTM
EVA
EOG
EQT
XOM
HAL
HES
DINO
KMI
MRO
MPC
NFE
NOV
OXY
OKE
OVV
PDCE
PSX
PXD
RRC
SLB
SWN
TRGP
TPL
VLO
VTS
WMB
AES
LNT
AEE
AEP
AWK
ATO
AGR
BEPC
CNP
CMS
ED
CEG
D
DTE
DUK
EIX
ETR
WTRG
EVRG
ES
EXC
FE
HE
IDA
MDU
NFG
NEE
NI
NRG
OGE
PCG
PNW
PPL
PEG
SRE
SO
UGI
VST
WEC
XEL
ATVI
GOOG
ATUS
AMC
T
CABO
CHTR
CMCSA
DISH
DIS
EA
FOXA
FOX
FYBR
IAC
IPG
LBRDA
LBRDK
FWONA
FWONK
LSXMA
LSXMK
LYV
LUMN
MSGS
MTCH
META
NFLX
NYT
NWSA
NWS
NXST
OMC
PARAA
PARA
PINS
PLTK
RBLX
ROKU
SIRI
SPOT
TMUS
TTWO
TRIP
VZ
WBD
WWE
ZI
ADM
ACI
MO
BJ
SAM
BF-A
BG
CPB
CASY
CHD
CLX
KO
CL
CAG
STZ
COST
COTY
DAR
DG
DLTR
EL
FLO
FRPT
GIS
GO
HSY
HRL
INGR
K
KDP
KMB
KHC
KR
LW
MKC
TAP
MDLZ
MNST
OLPX
PEP
PFGC
PM
PPC
POST
PG
REYN
SEB
SJM
SPB
SYY
TGT
TSN
USFD
WBA
WMT
APD
ALB
AA
AMCR
ATR
AMBP
ASH
AVY
AXTA
BALL
BERY
CE
CF
CC
CLF
CTVA
CCK
DOW
DD
EXP
EMN
ECL
ESI
FMC
FCX
DNA
GPK
HUN
IFF
IP
LIN
LPX
LYB
MLM
MOS
MP
NEU
NEM
NUE
OLN
PKG
PPG
RS
RGLD
RPM
SMG
SEE
SHW
SLGN
SON
SCCO
SSRM
STLD
X
VVV
VMC
WLK
WRK
ARE
AMH
A

In [2]:
df = cash_sheets.copy()

NameError: name 'cash_sheets' is not defined

In [1]:
df

NameError: name 'df' is not defined

In [8]:
len(df['company'].unique())

848

In [9]:
# Remove sectors, industries and individual companies previously identified for removal.

# Note: as we go through the analysis of the data for each of the financial statements, companies, industries and 
# sectors are identified for removal and stored in drop_data_details. 

for sector in drop_data_details['sector']:
   print(sector)
   df.drop(df[df['yahoo_sector'] == sector].index, inplace=True, axis=0)
    
for industry in drop_data_details['industry']:
   print(industry)
   df.drop(df[df['industry'] == industry].index, inplace=True, axis=0)
    
for company in drop_data_details['companies']:
   print(company)
   df.drop(df[df['company'] == company].index, inplace=True, axis=0)

Real Estate
Healthcare Plans
Healthcare Plans
Healthcare Plans
FOXA
LBRDK
FWONK
LSXMK
FWONK
LSXMK
UAA
ZG
PARAA
NWSA
BEPC
FWONA
LSXMA
CHK
VTS
BF-A
CASY
CAG
GIS
LW
RGLD
RPM
CTAS
CXT
FDX
OSK
PAYX
AZPN
KD
ORCL
PYCR
HRB
DRI
NKE
UA
DH
FYBR
DNB
BKI
DNB
BKI
DNB
BKI
DNB
BKI
CACI
CSX


In [10]:
list(df.columns.sort_values())

['amortizationCashFlow',
 'amortizationOfIntangibles',
 'amortizationOfSecurities',
 'assetImpairmentCharge',
 'beginningCashPosition',
 'capitalExpenditure',
 'capitalExpenditureReported',
 'cashDividendsPaid',
 'cashFlowFromContinuingFinancingActivities',
 'cashFlowFromContinuingInvestingActivities',
 'cashFlowFromContinuingOperatingActivities',
 'cashFlowFromDiscontinuedOperation',
 'cashFlowsfromusedinOperatingActivitiesDirect',
 'cashFromDiscontinuedFinancingActivities',
 'cashFromDiscontinuedInvestingActivities',
 'cashFromDiscontinuedOperatingActivities',
 'changeInAccountPayable',
 'changeInAccruedExpense',
 'changeInCashSupplementalAsReported',
 'changeInDividendPayable',
 'changeInIncomeTaxPayable',
 'changeInInterestPayable',
 'changeInInventory',
 'changeInOtherCurrentAssets',
 'changeInOtherCurrentLiabilities',
 'changeInOtherWorkingCapital',
 'changeInPayable',
 'changeInPayablesAndAccruedExpense',
 'changeInPrepaidAssets',
 'changeInReceivables',
 'changeInTaxPayable',
 

In [87]:
is_col_name_mapping = {'cf_accountsPayable': 'changeInPayablesAndAccruedExpense',
                       'cf_accountsReceivables': 'changeInReceivables'}

final = ['company', 'yahoo_sector','industry','st_date', 
         'netIncome',
         'capitalExpenditure',
         'beginningCashPosition',
         'endCashPosition',
         'depreciationAmortizationDepletion',
         'stockBasedCompensation',
         'changeInPayablesAndAccruedExpense',
         'changeInReceivables',
         'cashFlowFromContinuingOperatingActivities',
         'netBusinessPurchaseAndSale',
         'netPPEPurchaseAndSale',
         'netInvestmentPurchaseAndSale',
         'netIntangiblesPurchaseAndSale',
         'netOtherInvestingChanges',
         'cashFlowFromContinuingInvestingActivities',
         'netShortTermDebtIssuance',
         'netLongTermDebtIssuance',
         'netIssuancePaymentsOfDebt',
         'netOtherFinancingCharges',
         'netCommonStockIssuance',     
         'repurchaseOfCapitalStock',
         'cashDividendsPaid',
         'cashFlowFromContinuingFinancingActivities',      
         'freeCashFlow']

summary=['company', 'yahoo_sector','industry','st_date', 
         'netIncome', 
         'changeInWorkingCapital',
         'capitalExpenditure',
         'beginningCashPosition',
         'endCashPosition',
         'operatingCashFlow',
         'cashFlowFromContinuingOperatingActivities',
         'cashFlowFromContinuingInvestingActivities',
         'cashFlowFromContinuingFinancingActivities',
         'purchaseOfBusiness',
         'purchaseOfPPE',
         'repaymentOfDebt',
         'repurchaseOfCapitalStock',
         'cashDividendsPaid',
         'commonStockDividendPaid',
         'gainLossOnSaleOfBusiness',
         'saleOfPPE',
         'freeCashFlow']

operating=['company', 'yahoo_sector','industry','st_date', 
           'netIncome',
           'netIncomeFromContinuingOperations',
           'operatingGainsLosses',
           'depreciation',
           'depreciationAmortizationDepletion',
           'depreciationAndAmortization',
           'stockBasedCompensation',
           'deferredIncomeTax',
           'changeInInterestPayable',
           'changeInWorkingCapital',
           'changeInOtherWorkingCapital',
           'changesInAccountReceivables',
           'changeInReceivables',
           'changeInAccountPayable',
           'changeInPayable',
           'paymentstoSuppliersforGoodsandServices',
           'changeInPayablesAndAccruedExpense',
           'otherCashPaymentsfromOperatingActivities',
           'otherCashReceiptsfromOperatingActivities',
           'otherNonCashItems',
           'cashFlowsfromusedinOperatingActivitiesDirect',
           'cashFlowFromContinuingOperatingActivities']

investing=['company','yahoo_sector','industry','st_date', 
           'capitalExpenditure',
           'capitalExpenditureReported',
           'cashFlowFromContinuingInvestingActivities',
           'purchaseOfBusiness',
           'saleOfBusiness',
           'netBusinessPurchaseAndSale',
           'purchaseOfPPE',
           'saleOfPPE',
           'netPPEPurchaseAndSale',
           'purchaseOfInvestmentProperties',
           'saleOfInvestmentProperties',     
           'netInvestmentPropertiesPurchaseAndSale',
           'purchaseOfInvestment',
           'saleOfInvestment',
           'netInvestmentPurchaseAndSale',
           'purchaseOfIntangibles',
           'saleOfIntangibles',
           'netIntangiblesPurchaseAndSale',
           'netOtherInvestingChanges',
           'investingCashFlow']

finance=['company','yahoo_sector','industry','st_date', 
         'shortTermDebtIssuance',
         'shortTermDebtPayments',
         'netShortTermDebtIssuance', 
         'longTermDebtIssuance',
         'longTermDebtPayments',
         'netLongTermDebtIssuance',
         'issuanceOfDebt',
         'repaymentOfDebt',
         'netIssuancePaymentsOfDebt',
         'cashDividendsPaid',
         'commonStockDividendPaid',
         'preferredStockDividendPaid',
         'commonStockIssuance',
         'commonStockPayments',
         'netCommonStockIssuance',      
         'issuanceOfCapitalStock',
         'netPreferredStockIssuance',
         'netOtherFinancingCharges',
         'repurchaseOfCapitalStock']

adhoc=['company','yahoo_sector','industry',
       'st_date', 
       'cashFlowFromContinuingOperatingActivities',
       'capitalExpenditure',
       'freeCashFlow']

In [12]:
# Identify companies which have less than 4 years of data

len(df.groupby('company').filter(lambda x: len(x) < 4))

0

In [13]:
df.groupby('company').filter(lambda x: len(x) > 4)[summary]

company yahoo_sector                                industry     st_date   
0         AM       Energy                     Oil & Gas Midstream  2022-12-31  \
1         AM       Energy                     Oil & Gas Midstream  2023-03-31   
2         AM       Energy                     Oil & Gas Midstream  2019-12-31   
3         AM       Energy                     Oil & Gas Midstream  2020-12-31   
4         AM       Energy                     Oil & Gas Midstream  2021-12-31   
...      ...          ...                                     ...         ...   
4463     ZTS   Healthcare  Drug Manufacturers—Specialty & Generic  2022-12-31   
4464     ZTS   Healthcare  Drug Manufacturers—Specialty & Generic  2023-03-31   
4465     ZTS   Healthcare  Drug Manufacturers—Specialty & Generic  2019-12-31   
4466     ZTS   Healthcare  Drug Manufacturers—Specialty & Generic  2020-12-31   
4467     ZTS   Healthcare  Drug Manufacturers—Specialty & Generic  2021-12-31   

         netIncome  changeInWorkingCapital  capitalExpenditure   
0     326242000.00              5064000.00       -515650000.00  \
1     332709000.00            -19648000.00       -474376000.00   
2    -355114000.00             23472000.00       -267383000.00   
3    -122527000.00               419000.00       -157931000.00   
4      78626000.00              4431000.00       -232825000.00   
...            ...                     ...                 ...   
4463 2114000000.00           -699000000.00       -586000000.00   
4464 2071000000.00           -469000000.00       -694000000.00   
4465 1500000000.00           -151000000.00       -460000000.00   
4466 1638000000.00            -85000000.00       -453000000.00   
4467 2037000000.00           -343000000.00       -477000000.00   

      beginningCashPosition  endCashPosition  operatingCashFlow   
0                      0.00             0.00       699604000.00  \
1                      0.00              NaN       697659000.00   
2                2822000.00       1235000.00       622387000.00   
3                1235000.00        640000.00       753382000.00   
4                 640000.00             0.00       709752000.00   
...                     ...              ...                ...   
4463          3485000000.00    3581000000.00      1912000000.00   
4464          3135000000.00    2145000000.00      2152000000.00   
4465          1602000000.00    1934000000.00      1795000000.00   
4466          1934000000.00    3604000000.00      2126000000.00   
4467          3604000000.00    3485000000.00      2213000000.00   

      cashFlowFromContinuingOperatingActivities   
0                                  699604000.00  \
1                                  697659000.00   
2                                  622387000.00   
3                                  753382000.00   
4                                  709752000.00   
...                                         ...   
4463                              1912000000.00   
4464                              2152000000.00   
4465                              1795000000.00   
4466                              2126000000.00   
4467                              2213000000.00   

      cashFlowFromContinuingInvestingActivities   
0                                 -493826000.00  \
1                                 -451831000.00   
2                                 -525675000.00   
3                                 -219231000.00   
4                                 -233242000.00   
...                                         ...   
4463                              -883000000.00   
4464                              -981000000.00   
4465                              -504000000.00   
4466                              -572000000.00   
4467                              -458000000.00   

      cashFlowFromContinuingFinancingActivities  purchaseOfBusiness   
0                                 -205778000.00                0.00  \
1                                 -245828000.00                 Na

In [14]:
# Check counts 

df.groupby('company').filter(lambda x: len(x) > 4).groupby('company').size().sort_values()

company
LEG      5
NATI     5
NBIX     5
NCLH     5
NCNO     5
NCR      5
NEE      5
NEM      5
NET      5
NEU      5
NEWR     5
NFLX     5
NI       5
NOC      5
NOV      5
NOW      5
MTZ      5
NRG      5
MTN      5
MSI      5
MIDD     5
MKC      5
MKSI     5
MLM      5
MMM      5
MNST     5
MOS      5
MP       5
MPC      5
MRK      5
MRNA     5
MRO      5
MRVI     5
MRVL     5
MSA      5
MTD      5
NSC      5
NTAP     5
NVDA     5
PCG      5
PCOR     5
PDCE     5
PEG      5
PEGA     5
PEN      5
PENN     5
PEP      5
PFE      5
PHM      5
PII      5
PINS     5
PKG      5
PLNT     5
PLUG     5
PCAR     5
PAYC     5
PARA     5
OXY      5
NVR      5
NVST     5
NVT      5
NWL      5
NYT      5
OC       5
ODFL     5
MHK      5
OGE      5
OKE      5
OKTA     5
OLN      5
OLPX     5
OMC      5
ORLY     5
OTIS     5
OGN      5
MGM      5
META     5
MDU      5
ITW      5
JAMF     5
JAZZ     5
JBHT     5
JNJ      5
JNPR     5
JWN      5
K        5
KHC      5
KMB      5
KMI      5
KMX      5
KN

We know from analysis of data for income sheets that the unexpected extra rows corespond to spurious quarterly 
accounts plus TTM.

Delete rows which do not match the annual anniversary of statement date. This is determined by finding the most 
common month for a given company.

In [15]:
df = ext.remove_non_annual_data(df)

AM
AR
APA
BKR
LNG
CVX
COP
CTRA
DVN
FANG
DTM
EVA
EOG
EQT
XOM
HAL
HES
DINO
KMI
MRO
MPC
NFE
NOV
OXY
OKE
OVV
PDCE
PSX
PXD
RRC
SLB
SWN
TRGP
TPL
VLO
WMB
AES
LNT
AEE
AEP
AWK
ATO
AGR
CNP
CMS
ED
CEG
D
DTE
DUK
EIX
ETR
WTRG
EVRG
ES
EXC
FE
HE
IDA
MDU
NFG
NEE
NI
NRG
OGE
PCG
PNW
PPL
PEG
SRE
SO
UGI
VST
WEC
XEL
ATVI
GOOG
ATUS
AMC
T
CABO
CHTR
CMCSA
DISH
DIS
EA
FOX
IAC
IPG
LBRDA
LYV
LUMN
MSGS
MTCH
META
NFLX
NYT
NWS
NXST
OMC
PARA
PINS
PLTK
RBLX
ROKU
SIRI
SPOT
TMUS
TTWO
TRIP
VZ
WBD
WWE
ZI
ADM
ACI
MO
BJ
SAM
BG
CPB
CHD
CLX
KO
CL
STZ
COST
COTY
DAR
DG
DLTR
EL
FLO
FRPT
GO
HSY
HRL
INGR
K
KDP
KMB
KHC
KR
MKC
TAP
MDLZ
MNST
OLPX
PEP
PFGC
PM
PPC
POST
PG
REYN
SEB
SJM
SPB
SYY
TGT
TSN
USFD
WBA
WMT
APD
ALB
AA
AMCR
ATR
AMBP
ASH
AVY
AXTA
BALL
BERY
CE
CF
CC
CLF
CTVA
CCK
DOW
DD
EXP
EMN
ECL
ESI
FMC
FCX
DNA
GPK
HUN
IFF
IP
LIN
LPX
LYB
MLM
MOS
MP
NEU
NEM
NUE
OLN
PKG
PPG
RS
SMG
SEE
SHW
SLGN
SON
SCCO
SSRM
STLD
X
VVV
VMC
WLK
WRK
Z
MMM
AYI
ADP
WMS
ACM
AGCO
AL
ALK
ALLE
ALSN
AAL
AME
AWI
CAR
AXON
AZEK
BA
BAH
BR
BLDR
BWXT
CHRW
CSL
CARR

In [16]:
# Let's see if that leaves us with companies with less than 4 years of accounts

df.groupby('company').filter(lambda x: len(x) < 4)

Empty DataFrame
Columns: [st_date, amortizationCashFlow, amortizationOfIntangibles, assetImpairmentCharge, beginningCashPosition, capitalExpenditure, cashDividendsPaid, cashFlowFromContinuingFinancingActivities, cashFlowFromContinuingInvestingActivities, cashFlowFromContinuingOperatingActivities, changeInAccountPayable, changeInAccruedExpense, changeInCashSupplementalAsReported, changeInOtherCurrentAssets, changeInPayable, changeInPayablesAndAccruedExpense, changeInReceivables, changeInWorkingCapital, changesInAccountReceivables, commonStockDividendPaid, commonStockPayments, deferredIncomeTax, deferredTax, depreciation, depreciationAmortizationDepletion, depreciationAndAmortization, dividendReceivedCFO, earningsLossesFromEquityInvestments, endCashPosition, financingCashFlow, freeCashFlow, incomeTaxPaidSupplementalData, interestPaidSupplementalData, investingCashFlow, issuanceOfDebt, longTermDebtIssuance, longTermDebtPayments, netBusinessPurchaseAndSale, netCommonStockIssuance, netIncome, netIncomeFromContinuingOperations, netIssuancePaymentsOfDebt, netLongTermDebtIssuance, netOtherFinancingCharges, netOtherInvestingChanges, netPPEPurchaseAndSale, netShortTermDebtIssuance, operatingCashFlow, operatingGainsLosses, otherNonCashItems, preferredStockDividendPaid, purchaseOfBusiness, purchaseOfPPE, repaymentOfDebt, repurchaseOfCapitalStock, saleOfBusiness, stockBasedCompensation, changeInIncomeTaxPayable, changeInTaxPayable, changesInCash, dividendsReceivedCFI, shortTermDebtPayments, company, industry, yahoo_sector, gics_sector, st_YR, st_Mnth, changeInDividendPayable, changeInOtherCurrentLiabilities, commonStockIssuance, depletion, gainLossOnInvestmentSecurities, gainLossOnSaleOfBusiness, issuanceOfCapitalStock, otherCashAdjustmentOutsideChangeinCash, changeInPrepaidAssets, changeInInventory, changeInOtherWorkingCapital, netInvestmentPurchaseAndSale, saleOfInvestment, saleOfPPE, shortTermDebtIssuance, capitalExpenditureReported, effectOfExchangeRateChanges, unrealizedGainLossOnInvestmentSecurities, interestPaidCFO, gainLossOnSaleOfPPE, netForeignCurrencyExchangeGainLoss, proceedsFromStockOptionExercised, purchaseOfInvestment, changeInInterestPayable, netPreferredStockIssuance, preferredStockPayments, cashFlowFromDiscontinuedOperation, cashFromDiscontinuedFinancingActivities, cashFromDiscontinuedInvestingActivities, cashFromDiscontinuedOperatingActivities, netInvestmentPropertiesPurchaseAndSale, purchaseOfInvestmentProperties, ...]
Index: []

In [17]:
# Sanity check. Do we still have companies with more than 4.

df.groupby('company').filter(lambda x: len(x) > 4)

Empty DataFrame
Columns: [st_date, amortizationCashFlow, amortizationOfIntangibles, assetImpairmentCharge, beginningCashPosition, capitalExpenditure, cashDividendsPaid, cashFlowFromContinuingFinancingActivities, cashFlowFromContinuingInvestingActivities, cashFlowFromContinuingOperatingActivities, changeInAccountPayable, changeInAccruedExpense, changeInCashSupplementalAsReported, changeInOtherCurrentAssets, changeInPayable, changeInPayablesAndAccruedExpense, changeInReceivables, changeInWorkingCapital, changesInAccountReceivables, commonStockDividendPaid, commonStockPayments, deferredIncomeTax, deferredTax, depreciation, depreciationAmortizationDepletion, depreciationAndAmortization, dividendReceivedCFO, earningsLossesFromEquityInvestments, endCashPosition, financingCashFlow, freeCashFlow, incomeTaxPaidSupplementalData, interestPaidSupplementalData, investingCashFlow, issuanceOfDebt, longTermDebtIssuance, longTermDebtPayments, netBusinessPurchaseAndSale, netCommonStockIssuance, netIncome, netIncomeFromContinuingOperations, netIssuancePaymentsOfDebt, netLongTermDebtIssuance, netOtherFinancingCharges, netOtherInvestingChanges, netPPEPurchaseAndSale, netShortTermDebtIssuance, operatingCashFlow, operatingGainsLosses, otherNonCashItems, preferredStockDividendPaid, purchaseOfBusiness, purchaseOfPPE, repaymentOfDebt, repurchaseOfCapitalStock, saleOfBusiness, stockBasedCompensation, changeInIncomeTaxPayable, changeInTaxPayable, changesInCash, dividendsReceivedCFI, shortTermDebtPayments, company, industry, yahoo_sector, gics_sector, st_YR, st_Mnth, changeInDividendPayable, changeInOtherCurrentLiabilities, commonStockIssuance, depletion, gainLossOnInvestmentSecurities, gainLossOnSaleOfBusiness, issuanceOfCapitalStock, otherCashAdjustmentOutsideChangeinCash, changeInPrepaidAssets, changeInInventory, changeInOtherWorkingCapital, netInvestmentPurchaseAndSale, saleOfInvestment, saleOfPPE, shortTermDebtIssuance, capitalExpenditureReported, effectOfExchangeRateChanges, unrealizedGainLossOnInvestmentSecurities, interestPaidCFO, gainLossOnSaleOfPPE, netForeignCurrencyExchangeGainLoss, proceedsFromStockOptionExercised, purchaseOfInvestment, changeInInterestPayable, netPreferredStockIssuance, preferredStockPayments, cashFlowFromDiscontinuedOperation, cashFromDiscontinuedFinancingActivities, cashFromDiscontinuedInvestingActivities, cashFromDiscontinuedOperatingActivities, netInvestmentPropertiesPurchaseAndSale, purchaseOfInvestmentProperties, ...]
Index: []

In [18]:
# Check count of companies

len(df['company'].unique())

737

## Operating Activities

In [19]:
df[operating].isnull().sum().sort_values()

company                                            0
yahoo_sector                                       0
industry                                           0
st_date                                            0
netIncome                                          0
changeInWorkingCapital                             1
depreciationAmortizationDepletion                  1
cashFlowFromContinuingOperatingActivities          1
netIncomeFromContinuingOperations                  1
changeInPayablesAndAccruedExpense                 54
changeInReceivables                              118
depreciationAndAmortization                      142
otherNonCashItems                                216
deferredIncomeTax                                299
stockBasedCompensation                           320
changeInPayable                                  459
changeInAccountPayable                           509
operatingGainsLosses                             627
changeInOtherWorkingCapital                   

In [20]:
df[df['cashFlowFromContinuingOperatingActivities'].isnull()].sort_values(by=['industry','company','st_date'])[summary]

company yahoo_sector                   industry     st_date    netIncome   
2337    UHAL  Industrials  Rental & Leasing Services  2023-03-31 922998000.00  \

      changeInWorkingCapital  capitalExpenditure  beginningCashPosition   
2337                     NaN                 NaN                    NaN  \

      endCashPosition  operatingCashFlow   
2337              NaN                NaN  \

      cashFlowFromContinuingOperatingActivities   
2337                                        NaN  \

      cashFlowFromContinuingInvestingActivities   
2337                                        NaN  \

      cashFlowFromContinuingFinancingActivities  purchaseOfBusiness   
2337                                        NaN                 NaN  \

      purchaseOfPPE  repaymentOfDebt  repurchaseOfCapitalStock   
2337            NaN              NaN                       NaN  \

      cashDividendsPaid  commonStockDividendPaid  gainLossOnSaleOfBusiness   
2337                NaN                      NaN                       NaN  \

      saleOfPPE  freeCashFlow  
2337        NaN           NaN

UHAL - Data for 2023 is missing. Verified this is the case by check Yahoo Finance website. 

Delete this company.

In [21]:
drop_data_details['companies'] = drop_data_details['companies'] + ['UHAL']
df.drop(df[df['company'] == 'UHAL'].index, inplace=True, axis=0)

In [22]:
df[df['changeInPayablesAndAccruedExpense'].isnull()].sort_values(by=['industry','company','st_date'])[operating]

company       yahoo_sector                        industry     st_date   
1632     ALK        Industrials                        Airlines  2019-12-31  \
1633     ALK        Industrials                        Airlines  2020-12-31   
1634     ALK        Industrials                        Airlines  2021-12-31   
1635     ALK        Industrials                        Airlines  2022-12-31   
4362    SGEN         Healthcare                   Biotechnology  2019-12-31   
4363    SGEN         Healthcare                   Biotechnology  2020-12-31   
4364    SGEN         Healthcare                   Biotechnology  2021-12-31   
4360    SGEN         Healthcare                   Biotechnology  2022-12-31   
897      SEB        Industrials                   Conglomerates  2019-12-31   
1843     EFX        Industrials             Consulting Services  2019-12-31   
1844     EFX        Industrials             Consulting Services  2020-12-31   
1845     EFX        Industrials             Consulting Services  2021-12-31   
1841     EFX        Industrials             Consulting Services  2022-12-31   
3363    CHDN  Consumer Cyclical                        Gambling  2019-12-31   
3364    CHDN  Consumer Cyclical                        Gambling  2020-12-31   
3365    CHDN  Consumer Cyclical                        Gambling  2021-12-31   
3361    CHDN  Consumer Cyclical                        Gambling  2022-12-31   
3356     CHH  Consumer Cyclical                         Lodging  2019-12-31   
3357     CHH  Consumer Cyclical                         Lodging  2020-12-31   
3358     CHH  Consumer Cyclical                         Lodging  2021-12-31   
3359     CHH  Consumer Cyclical                         Lodging  2022-12-31   
3571     MAR  Consumer Cyclical                         Lodging  2019-12-31   
3572     MAR  Consumer Cyclical                         Lodging  2020-12-31   
3573     MAR  Consumer Cyclical                         Lodging  2021-12-31   
3569     MAR  Consumer Cyclical                         Lodging  2022-12-31   
977     AMBP  Consumer Cyclical          Packaging & Containers  2019-12-31   
975     AMBP  Consumer Cyclical          Packaging & Containers  2020-12-31   
978     AMBP  Consumer Cyclical          Packaging & Containers  2021-12-31   
976     AMBP  Consumer Cyclical          Packaging & Containers  2022-12-31   
2107     NSC        Industrials                       Railroads  2019-12-31   
2108     NSC        Industrials                       Railroads  2020-12-31   
2109     NSC        Industrials                       Railroads  2021-12-31   
2110     NSC        Industrials                       Railroads  2022-12-31   
3003    PEGA         Technology            Software—Application  2021-12-31   
2999    PEGA         Technology            Software—Application  2022-12-31   
2059     MAN        Industrials  Staffing & Employment Services  2019-12-31   
2060     MAN        Industrials  Staffing & Employment Services  2020-12-31   
2061     MAN        Industrials  Staffing & Employment Services  2021-12-31   
2062     MAN        Industrials  Staffing & Employment Services  2022-12-31   
3291    BKNG  Consumer Cyclical                 Travel Services  2020-12-31   
3292    BKNG  Consumer Cyclical                 Travel Services  2021-12-31   
3289    BKNG  Consumer Cyclical                 Travel Services  2022-12-31   
229      AGR          Utilities    Utilities—Regulated Electric  2019-12-31   
230      AGR          Utilities    Utilities—Regulated Electric  2020-12-31   
231      AGR          Utilities    Utilities—Regulated Electric  2021-12-31   
227      AGR          Utilities    Utilities—Regulated Electric  2022-12-31   
203      LNT          Utilities    Utilities—Regulated Electric  2019-12-31   
204      LNT          Utilities    Utilities—Regulated Electric  2020-12-31   
202      LNT          Utilities    Utilities—Regulated Electric  2021-12-31   
328      NEE          Utilities    Utilities—Regulated 

Scrollling down, we are able to verify that where changeInPayablesAndAccruedExpense is null, so are related 
fields, so we cannot derive change in accounts payable. Of the fields available, changeInPayablesAndAccruedExpense
is the one we with the best count and one we can include in the final dataset.

In [26]:
df[df['changeInReceivables'].isnull()].sort_values(by=['industry','company','st_date'])[operating]

company            yahoo_sector                      industry   
3443     GPS       Consumer Cyclical                Apparel Retail  \
3444     GPS       Consumer Cyclical                Apparel Retail   
3445     GPS       Consumer Cyclical                Apparel Retail   
3446     GPS       Consumer Cyclical                Apparel Retail   
3561    LULU       Consumer Cyclical                Apparel Retail   
3558    LULU       Consumer Cyclical                Apparel Retail   
3559    LULU       Consumer Cyclical                Apparel Retail   
3560    LULU       Consumer Cyclical                Apparel Retail   
3707    ROST       Consumer Cyclical                Apparel Retail   
3708    ROST       Consumer Cyclical                Apparel Retail   
3709    ROST       Consumer Cyclical                Apparel Retail   
3706    ROST       Consumer Cyclical                Apparel Retail   
3704    RIVN       Consumer Cyclical            Auto Manufacturers   
3687      QS       Consumer Cyclical                    Auto Parts   
3689      QS       Consumer Cyclical                    Auto Parts   
3688      QS       Consumer Cyclical                    Auto Parts   
3686      QS       Consumer Cyclical                    Auto Parts   
4234    MRTX              Healthcare                 Biotechnology   
4235    MRTX              Healthcare                 Biotechnology   
4236    MRTX              Healthcare                 Biotechnology   
4261    NVAX              Healthcare                 Biotechnology   
3192      WU      Financial Services               Credit Services   
3193      WU      Financial Services               Credit Services   
3194      WU      Financial Services               Credit Services   
3195      WU      Financial Services               Credit Services   
3509     KSS       Consumer Cyclical             Department Stores   
3507     KSS       Consumer Cyclical             Department Stores   
3508     KSS       Consumer Cyclical             Department Stores   
3505     KSS       Consumer Cyclical             Department Stores   
734     COST      Consumer Defensive               Discount Stores   
735     COST      Consumer Defensive               Discount Stores   
736     COST      Consumer Defensive               Discount Stores   
737     COST      Consumer Defensive               Discount Stores   
754       DG      Consumer Defensive               Discount Stores   
755       DG      Consumer Defensive               Discount Stores   
756       DG      Consumer Defensive               Discount Stores   
752       DG      Consumer Defensive               Discount Stores   
757     DLTR      Consumer Defensive               Discount Stores   
758     DLTR      Consumer Defensive               Discount Stores   
759     DLTR      Consumer Defensive               Discount Stores   
760     DLTR      Consumer Defensive               Discount Stores   
921      TGT      Consumer Defensive               Discount Stores   
922      TGT      Consumer Defensive               Discount Stores   
923      TGT      Consumer Defensive               Discount Stores   
924      TGT      Consumer Defensive               Discount Stores   
553     NFLX  Communication Services                 Entertainment   
554     NFLX  Communication Services                 Entertainment   
555     NFLX  Communication Services                 Entertainment   
551     NFLX  Communication Services                 Entertainment   
3365    CHDN       Consumer Cyclical                      Gambling   
3361    CHDN       Consumer Cyclical                      Gambling   
3547     LOW       Consumer Cyclical       Home Improvement Retail   
3548     LOW       Consumer Cyclical       Home Improvement Retail   
3549     LOW       Consumer Cyclical       Home Improvement Retail   
3550     LOW       Consumer Cyclical       Home Improvement Retail   
3408    EBAY       Consumer Cyclical               Internet Retail   
3356     CHH   

Verified that alternative fields are also null. Conclude that cahngeInReceivables is the best one to use in final
data set and some values will be null.

In [91]:
operating

['company',
 'yahoo_sector',
 'industry',
 'st_date',
 'netIncome',
 'netIncomeFromContinuingOperations',
 'operatingGainsLosses',
 'depreciation',
 'depreciationAmortizationDepletion',
 'depreciationAndAmortization',
 'stockBasedCompensation',
 'deferredIncomeTax',
 'changeInInterestPayable',
 'changeInWorkingCapital',
 'changeInOtherWorkingCapital',
 'changesInAccountReceivables',
 'changeInReceivables',
 'changeInAccountPayable',
 'changeInPayable',
 'paymentstoSuppliersforGoodsandServices',
 'changeInPayablesAndAccruedExpense',
 'otherCashPaymentsfromOperatingActivities',
 'otherCashReceiptsfromOperatingActivities',
 'otherNonCashItems',
 'cashFlowsfromusedinOperatingActivitiesDirect',
 'cashFlowFromContinuingOperatingActivities']

In [94]:
# Select fields for final cut

final_operating = ['netIncome',
                   'netIncomeFromContinuingOperations',
                   'depreciationAmortizationDepletion',
                   'stockBasedCompensation',
                   'cashFlowFromContinuingOperatingActivities']

is_col_name_mapping['cf_operatingIncome'] = ['netIncomeFromContinuingOperations']

## Investing

In [29]:
df[investing].isnull().sum().sort_values()

company                                         0
investingCashFlow                               0
cashFlowFromContinuingInvestingActivities       0
cashFlowFromContinuingInvestingActivities       0
st_date                                         0
industry                                        0
yahoo_sector                                    0
capitalExpenditure                             11
netBusinessPurchaseAndSale                    532
netPPEPurchaseAndSale                         696
purchaseOfBusiness                            701
netOtherInvestingChanges                      959
purchaseOfPPE                                1046
netInvestmentPurchaseAndSale                 1101
purchaseOfInvestment                         1364
saleOfInvestment                             1377
capitalExpenditureReported                   1565
saleOfPPE                                    1889
saleOfBusiness                               1935
purchaseOfIntangibles                        2383


In [32]:
df[df['capitalExpenditure'].isnull()].sort_values(by=['industry','company','st_date'])[investing]

company yahoo_sector                      industry     st_date   
4343    RPRX   Healthcare                 Biotechnology  2019-12-31  \
4344    RPRX   Healthcare                 Biotechnology  2020-12-31   
4345    RPRX   Healthcare                 Biotechnology  2021-12-31   
4346    RPRX   Healthcare                 Biotechnology  2022-12-31   
4435    VEEV   Healthcare   Health Information Services  2021-01-31   
4436    VEEV   Healthcare   Health Information Services  2022-01-31   
4432    VEEV   Healthcare   Health Information Services  2023-01-31   
203      LNT    Utilities  Utilities—Regulated Electric  2019-12-31   
204      LNT    Utilities  Utilities—Regulated Electric  2020-12-31   
202      LNT    Utilities  Utilities—Regulated Electric  2021-12-31   
200      LNT    Utilities  Utilities—Regulated Electric  2022-12-31   

      capitalExpenditure  capitalExpenditureReported   
4343                 NaN                         NaN  \
4344                 NaN                         NaN   
4345                 NaN                         NaN   
4346                 NaN                         NaN   
4435                 NaN                         NaN   
4436                 NaN                         NaN   
4432                 NaN                         NaN   
203                  NaN                         NaN   
204                  NaN                         NaN   
202                  NaN                         NaN   
200                  NaN                         NaN   

      cashFlowFromContinuingInvestingActivities   
4343                             -2116142000.00  \
4344                             -2759000000.00   
4345                             -1870280000.00   
4346                             -1029421000.00   
4435                              -333634000.00   
4436                              -346152000.00   
4432                             -1007683000.00   
203                              -1287300000.00   
204                               -951000000.00   
202                               -728000000.00   
200                               -933000000.00   

      netInvestmentPropertiesPurchaseAndSale  netInvestmentPurchaseAndSale   
4343                                     NaN                -1839100000.00  \
4344                                     NaN                -2734000000.00   
4345                                     NaN                -1817348000.00   
4346                                     NaN                -1019525000.00   
4435                                     NaN                 -324951000.00   
4436                                     NaN                 -324158000.00   
4432                                     NaN                 -994171000.00   
203                                      NaN                           NaN   
204                                      NaN                           NaN   
202                                      NaN                           NaN   
200                                      NaN                           NaN   

      netBusinessPurchaseAndSale  netPPEPurchaseAndSale  purchaseOfBusiness   
4343                -27042000.00                    NaN        -27042000.00  \
4344                -40000000.00                    NaN        -40000000.00   
4345                -34855000.00                    NaN        -34855000.00   
4346                 -9896000.00                    NaN         -9896000.00   
4435                        0.00                    NaN                0.00   
4436                 -7780000.00                    NaN         -7780000.00   
4432                        0.00                    NaN                0.00   
203               -1640100000.00                    NaN      -1640100000.00   
204               -1366000000.00                    NaN      -1366000000.00   
202               -1169000000.00                    NaN      -1169000000.00   
200               -1484000000.00                    NaN     

In [34]:
col_list=['company','st_date',
          'cashFlowFromContinuingOperatingActivities','capitalExpenditure','freeCashFlow']
df[df['company'].isin(['RPRX','VEEV','LNT'])][col_list].sort_values(by=['company','st_date'])

company     st_date  cashFlowFromContinuingOperatingActivities   
203      LNT  2019-12-31                               660400000.00  \
204      LNT  2020-12-31                               501000000.00   
202      LNT  2021-12-31                               582000000.00   
200      LNT  2022-12-31                               486000000.00   
4343    RPRX  2019-12-31                              1667239000.00   
4344    RPRX  2020-12-31                              2034629000.00   
4345    RPRX  2021-12-31                              2017536000.00   
4346    RPRX  2022-12-31                              2143980000.00   
4434    VEEV  2020-01-31                               437375000.00   
4435    VEEV  2021-01-31                               551246000.00   
4436    VEEV  2022-01-31                               764463000.00   
4432    VEEV  2023-01-31                               780470000.00   

      capitalExpenditure  freeCashFlow  
203                  NaN  660400000.00  
204                  NaN  501000000.00  
202                  NaN  582000000.00  
200                  NaN  486000000.00  
4343                 NaN 1667239000.00  
4344                 NaN 2035000000.00  
4345                 NaN 2017536000.00  
4346                 NaN 2143980000.00  
4434         -4321000.00  433054000.00  
4435                 NaN  551246000.00  
4436                 NaN  764463000.00  
4432                 NaN  780470000.00

Where CapEx is null, free cash flow is equal to operating cash flow. So we can deduce that capex is 0 if null.
Set capitalExpenditure to 0 if null on this basis.

In [35]:
df['capitalExpenditure'] = df['capitalExpenditure'].fillna(0)

In [38]:
df[df['netBusinessPurchaseAndSale'].isnull()].sort_values(by=['industry','company','st_date'])[investing]

company            yahoo_sector                                industry   
1682      BA             Industrials                     Aerospace & Defense  \
1679      BA             Industrials                     Aerospace & Defense   
1903      GD             Industrials                     Aerospace & Defense   
1904      GD             Industrials                     Aerospace & Defense   
1949     HWM             Industrials                     Aerospace & Defense   
1950     HWM             Industrials                     Aerospace & Defense   
1951     HWM             Industrials                     Aerospace & Defense   
1947     HWM             Industrials                     Aerospace & Defense   
1937     HXL             Industrials                     Aerospace & Defense   
2053     LMT             Industrials                     Aerospace & Defense   
2049     LMT             Industrials                     Aerospace & Defense   
1016      CF         Basic Materials                     Agricultural Inputs   
1017      CF         Basic Materials                     Agricultural Inputs   
1013      CF         Basic Materials                     Agricultural Inputs   
1128     MOS         Basic Materials                     Agricultural Inputs   
1130     MOS         Basic Materials                     Agricultural Inputs   
1648     AAL             Industrials                                Airlines   
1632     ALK             Industrials                                Airlines   
1633     ALK             Industrials                                Airlines   
1634     ALK             Industrials                                Airlines   
1635     ALK             Industrials                                Airlines   
1748     CPA             Industrials                                Airlines   
1749     CPA             Industrials                                Airlines   
1750     CPA             Industrials                                Airlines   
1751     CPA             Industrials                                Airlines   
1997    JBLU             Industrials                                Airlines   
1993    JBLU             Industrials                                Airlines   
1994    JBLU             Industrials                                Airlines   
2258     LUV             Industrials                                Airlines   
2259     LUV             Industrials                                Airlines   
2260     LUV             Industrials                                Airlines   
2261     LUV             Industrials                                Airlines   
2352     UAL             Industrials                                Airlines   
2349     UAL             Industrials                                Airlines   
961       AA         Basic Materials                                Aluminum   
962       AA         Basic Materials                                Aluminum   
963       AA         Basic Materials                                Aluminum   
959       AA         Basic Materials                                Aluminum   
3368    COLM       Consumer Cyclical                   Apparel Manufacturing   
3369    COLM       Consumer Cyclical                   Apparel Manufacturing   
3370    COLM       Consumer Cyclical                   Apparel Manufacturing   
3366    COLM       Consumer Cyclical                   Apparel Manufacturing   
3473     HBI       Consumer Cyclical                   Apparel Manufacturing   
3692      RL       Consumer Cyclical                   Apparel Manufacturing   
3693      RL       Consumer Cyclical                   Apparel Manufacturing   
3694      RL       Consumer Cyclical                   Apparel Manufacturing   
3316    BURL       Consumer Cyclical                          Apparel Retail   
3317    BURL       Consumer Cyclical                          Apparel Retail   
3318    BURL       Consumer Cyclical                          Apparel Retail   
3319 

We are interested in net spend on acquisitions and we can allow for any offsets resulting from disposals. So based
on count and verification from above, we can take netBusinessPurchaseAndSale as amount spent on acquisitions. If 
positive then it is amount resulting from disposals.

It's reasonable to set netBusinessPurchaseAndSale to 0 if null. I think it is fair to apply the same to purchaseOfBusiness
and saleOfBusiness.

In [39]:
df['netBusinessPurchaseAndSale'] = df['netBusinessPurchaseAndSale'].fillna(0)
df['purchaseOfBusiness'] = df['purchaseOfBusiness'].fillna(0)
df['saleOfBusiness'] = df['saleOfBusiness'].fillna(0)

In [59]:
df[df['netInvestmentPurchaseAndSale'].isnull()].sort_values(by=['industry','company','st_date'])[investing]

Empty DataFrame
Columns: [company, yahoo_sector, industry, st_date, capitalExpenditure, capitalExpenditureReported, cashFlowFromContinuingInvestingActivities, netBusinessPurchaseAndSale, purchaseOfBusiness, saleOfBusiness, netPPEPurchaseAndSale, netInvestmentPropertiesPurchaseAndSale, purchaseOfIntangibles, purchaseOfInvestment, purchaseOfInvestmentProperties, purchaseOfPPE, saleOfInvestmentProperties, saleOfPPE, saleOfIntangibles, purchaseOfInvestment, saleOfInvestment, netInvestmentPurchaseAndSale, purchaseOfIntangibles, saleOfIntangibles, netIntangiblesPurchaseAndSale, netOtherInvestingChanges, investingCashFlow, cashFlowFromContinuingInvestingActivities]
Index: []

In [43]:
df['netInvestmentPurchaseAndSale'] = df['netInvestmentPurchaseAndSale'].fillna(0)
df['purchaseOfInvestment'] = df['purchaseOfInvestment'].fillna(0)
df['saleOfInvestment'] = df['saleOfInvestment'].fillna(0)

In [42]:
df[df['netInvestmentPropertiesPurchaseAndSale'].isnull()].sort_values(by=['industry','company','st_date'])[investing]

company            yahoo_sector              industry     st_date   
484      IPG  Communication Services  Advertising Agencies  2019-12-31  \
485      IPG  Communication Services  Advertising Agencies  2020-12-31   
486      IPG  Communication Services  Advertising Agencies  2021-12-31   
487      IPG  Communication Services  Advertising Agencies  2022-12-31   
579      OMC  Communication Services  Advertising Agencies  2019-12-31   
...      ...                     ...                   ...         ...   
2277    SRCL             Industrials      Waste Management  2022-12-31   
2389      WM             Industrials      Waste Management  2019-12-31   
2390      WM             Industrials      Waste Management  2020-12-31   
2391      WM             Industrials      Waste Management  2021-12-31   
2392      WM             Industrials      Waste Management  2022-12-31   

      capitalExpenditure  capitalExpenditureReported   
484        -198500000.00               -198500000.00  \
485        -167500000.00               -167500000.00   
486        -195300000.00               -195300000.00   
487        -178100000.00               -178100000.00   
579        -102200000.00               -102200000.00   
...                  ...                         ...   
2277       -132200000.00               -132200000.00   
2389      -1818000000.00              -1818000000.00   
2390      -1632000000.00              -1632000000.00   
2391      -1904000000.00              -1904000000.00   
2392      -2587000000.00              -2587000000.00   

      cashFlowFromContinuingInvestingActivities  netBusinessPurchaseAndSale   
484                               -161700000.00                  -600000.00  \
485                               -216200000.00                 -4900000.00   
486                               -185300000.00                -16300000.00   
487                               -430100000.00               -252600000.00   
579                                -30900000.00                 69400000.00   
...                                         ...                         ...   
2277                               -84600000.00                 46700000.00   
2389                             -2376000000.00               -472000000.00   
2390                             -4847000000.00              -3200000000.00   
2391                             -1894000000.00                 21000000.00   
2392                             -3063000000.00               -350000000.00   

      purchaseOfBusiness  saleOfBusiness  netPPEPurchaseAndSale   
484           -600000.00            0.00                    NaN  \
485          -4900000.00            0.00                    NaN   
486         -16300000.00            0.00                    NaN   
487        -252600000.00            0.00                    NaN   
579         -10000000.00     79400000.00                    NaN   
...                  ...             ...                    ...   
2277                0.00     46700000.00                    NaN   
2389       -521000000.00     49000000.00                    NaN   
2390      -4085000000.00    885000000.00                    NaN   
2391        -75000000.00     96000000.00                    NaN   
2392       -377000000.00     27000000.00                    NaN   

      netInvestmentPropertiesPurchaseAndSale  purchaseOfIntangibles   
484                                      NaN                    NaN  \
485                                      NaN                    NaN   
486                                      NaN                    NaN   
487                                      NaN                    NaN   
579                                      NaN                    NaN   
...                                      ...                    ...   
2277                                     NaN                    NaN   
2389                                     NaN                    NaN   
2390                                     NaN      

In [56]:
df['netInvestmentPropertiesPurchaseAndSale'] = df['netInvestmentPropertiesPurchaseAndSale'].fillna(0)
df['purchaseOfInvestmentProperties'] = df['purchaseOfInvestmentProperties'].fillna(0)
df['saleOfInvestmentProperties'] = df['saleOfInvestmentProperties'].fillna(0)

In [50]:
df[df['netIntangiblesPurchaseAndSale'].notna()].sort_values(by=['industry','company','st_date'])[investing]

company            yahoo_sector                                industry   
1667    AXON             Industrials                     Aerospace & Defense  \
1668    AXON             Industrials                     Aerospace & Defense   
1669    AXON             Industrials                     Aerospace & Defense   
1670    AXON             Industrials                     Aerospace & Defense   
1681      BA             Industrials                     Aerospace & Defense   
2176     RTX             Industrials                     Aerospace & Defense   
2177     RTX             Industrials                     Aerospace & Defense   
2178     RTX             Industrials                     Aerospace & Defense   
2174     RTX             Industrials                     Aerospace & Defense   
1017      CF         Basic Materials                     Agricultural Inputs   
1013      CF         Basic Materials                     Agricultural Inputs   
1074     FMC         Basic Materials                     Agricultural Inputs   
1075     FMC         Basic Materials                     Agricultural Inputs   
1185     SMG         Basic Materials                     Agricultural Inputs   
1186     SMG         Basic Materials                     Agricultural Inputs   
1187     SMG         Basic Materials                     Agricultural Inputs   
1748     CPA             Industrials                                Airlines   
1749     CPA             Industrials                                Airlines   
1750     CPA             Industrials                                Airlines   
1751     CPA             Industrials                                Airlines   
3473     HBI       Consumer Cyclical                   Apparel Manufacturing   
3684     PVH       Consumer Cyclical                   Apparel Manufacturing   
3681     PVH       Consumer Cyclical                   Apparel Manufacturing   
3808     VFC       Consumer Cyclical                   Apparel Manufacturing   
3809     VFC       Consumer Cyclical                   Apparel Manufacturing   
3810     VFC       Consumer Cyclical                   Apparel Manufacturing   
3811     VFC       Consumer Cyclical                   Apparel Manufacturing   
3650     PAG       Consumer Cyclical                Auto & Truck Dealerships   
3651     PAG       Consumer Cyclical                Auto & Truck Dealerships   
3652     PAG       Consumer Cyclical                Auto & Truck Dealerships   
3653     PAG       Consumer Cyclical                Auto & Truck Dealerships   
3753    TSLA       Consumer Cyclical                      Auto Manufacturers   
3754    TSLA       Consumer Cyclical                      Auto Manufacturers   
3752    TSLA       Consumer Cyclical                      Auto Manufacturers   
3750    TSLA       Consumer Cyclical                      Auto Manufacturers   
3252    APTV       Consumer Cyclical                              Auto Parts   
3253    APTV       Consumer Cyclical                              Auto Parts   
685      SAM      Consumer Defensive                       Beverages—Brewers   
683      SAM      Consumer Defensive                       Beverages—Brewers   
811      KDP      Consumer Defensive                 Beverages—Non-Alcoholic   
812      KDP      Consumer Defensive                 Beverages—Non-Alcoholic   
813      KDP      Consumer Defensive                 Beverages—Non-Alcoholic   
809      KDP      Consumer Defensive                 Beverages—Non-Alcoholic   
850     MNST      Consumer Defensive                 Beverages—Non-Alcoholic   
851     MNST      Consumer Defensive                 Beverages—Non-Alcoholic   
852     MNST      Consumer Defensive                 Beverages—Non-Alcoholic   
848     MNST      Consumer Defensive                 Beverages—Non-Alcoholic   
3961    BMRN              Healthcare                           Biotechnology   
3962    BMRN              Healthcare                           Biotechnology   
3963 

Conclusion: purchase and sale of intangibles is significant. Net purchases and sales of intangibles is the best 
field to take in final cut. 

Reasonable to set fields to 0 where they are null.

In [54]:
df['netIntangiblesPurchaseAndSale'] = df['netIntangiblesPurchaseAndSale'].fillna(0)
df['purchaseOfIntangibles'] = df['purchaseOfIntangibles'].fillna(0)
df['saleOfIntangibles'] = df['saleOfIntangibles'].fillna(0)

In [60]:
df[df['netPPEPurchaseAndSale'].notna()].sort_values(by=['industry','company','st_date'])[investing]

company yahoo_sector             industry     st_date   
1667    AXON  Industrials  Aerospace & Defense  2019-12-31  \
1668    AXON  Industrials  Aerospace & Defense  2020-12-31   
1669    AXON  Industrials  Aerospace & Defense  2021-12-31   
1670    AXON  Industrials  Aerospace & Defense  2022-12-31   
1681      BA  Industrials  Aerospace & Defense  2019-12-31   
...      ...          ...                  ...         ...   
1745     CLH  Industrials     Waste Management  2022-12-31   
2184     RSG  Industrials     Waste Management  2019-12-31   
2185     RSG  Industrials     Waste Management  2020-12-31   
2186     RSG  Industrials     Waste Management  2021-12-31   
2187     RSG  Industrials     Waste Management  2022-12-31   

      capitalExpenditure  capitalExpenditureReported   
1667        -16343000.00                         NaN  \
1668        -72870000.00                         NaN   
1669        -50278000.00                         NaN   
1670        -56109000.00                         NaN   
1681      -1961000000.00                         NaN   
...                  ...                         ...   
1745       -347022000.00                         NaN   
2184      -1207100000.00                         NaN   
2185      -1194600000.00                         NaN   
2186      -1316300000.00                         NaN   
2187      -1454000000.00                         NaN   

      cashFlowFromContinuingInvestingActivities  netBusinessPurchaseAndSale   
1667                              -240737000.00                        0.00  \
1668                              -356526000.00                 -7068000.00   
1669                               252556000.00                -22393000.00   
1670                              -830967000.00                 -2104000.00   
1681                             -1530000000.00                  9000000.00   
...                                         ...                         ...   
1745                              -388944000.00                -69467000.00   
2184                             -1719000000.00               -532300000.00   
2185                             -1922800000.00               -736600000.00   
2186                             -2466100000.00              -1175400000.00   
2187                             -4423000000.00              -2987900000.00   

      purchaseOfBusiness  saleOfBusiness  netPPEPurchaseAndSale   
1667                0.00            0.00           -15939000.00  \
1668         -7068000.00            0.00           -72534000.00   
1669        -22393000.00            0.00           -49843000.00   
1670         -2104000.00            0.00           -55515000.00   
1681       -455000000.00    464000000.00         -1500000000.00   
...                  ...             ...                    ...   
1745        -86278000.00     16811000.00          -336277000.00   
2184       -575100000.00     42800000.00         -1185400000.00   
2185       -769500000.00     32900000.00         -1164500000.00   
2186      -1221700000.00     46300000.00         -1296800000.00   
2187      -3038500000.00     50600000.00         -1421200000.00   

      netInvestmentPropertiesPurchaseAndSale  purchaseOfIntangibles   
1667                                    0.00             -404000.00  \
1668                                    0.00             -241000.00   
1669                                    0.00             -392000.00   
1670                                    0.00             -307000.00   
1681                                    0.00          -127000000.00   
...                                      ...                    ...   
1745                                    0.00            -1966000.00   
2184                                    0.00                   0.00   
2185                                    0.00                   0.00   
2186                                    0.00                   0.00   
2187                                    0.00        

In [62]:
df['netPPEPurchaseAndSale'] = df['netPPEPurchaseAndSale'].fillna(0)
df['purchaseOfPPE'] = df['purchaseOfPPE'].fillna(0)
df['saleOfPPE'] = df['saleOfPPE'].fillna(0)

In [63]:
# Check count of nulls to see what's left

df[investing].isnull().sum().sort_values()

company                                         0
netIntangiblesPurchaseAndSale                   0
saleOfIntangibles                               0
purchaseOfIntangibles                           0
netInvestmentPurchaseAndSale                    0
saleOfInvestment                                0
purchaseOfInvestment                            0
saleOfIntangibles                               0
saleOfPPE                                       0
saleOfInvestmentProperties                      0
purchaseOfPPE                                   0
purchaseOfInvestmentProperties                  0
investingCashFlow                               0
purchaseOfInvestment                            0
netInvestmentPropertiesPurchaseAndSale          0
netPPEPurchaseAndSale                           0
saleOfBusiness                                  0
purchaseOfBusiness                              0
netBusinessPurchaseAndSale                      0
cashFlowFromContinuingInvestingActivities       0


In [64]:
df['netOtherInvestingChanges'] = df['netOtherInvestingChanges'].fillna(0)

In [96]:
# Select fields for final cut

final_investing = ['capitalExpenditure', 
                   'netBusinessPurchaseAndSale',
                   'netPPEPurchaseAndSale',
                   'netInvestmentPropertiesPurchaseAndSale',
                   'netInvestmentPurchaseAndSale',
                   'netIntangiblesPurchaseAndSale',
                   'cashFlowFromContinuingInvestingActivities']

is_col_name_mapping['cf_investingCashFlow'] = 'cashFlowFromContinuingInvestingActivities'
is_col_name_mapping['cf_netAcquisitions'] = 'netBusinessPurchaseAndSale'

## Finance

In [67]:
df[finance].isnull().sum().sort_values()

company                         0
yahoo_sector                    0
industry                        0
st_date                         0
netIssuancePaymentsOfDebt     111
netLongTermDebtIssuance       159
repaymentOfDebt               188
longTermDebtPayments          257
issuanceOfDebt                290
netOtherFinancingCharges      311
netCommonStockIssuance        311
longTermDebtIssuance          394
repurchaseOfCapitalStock      667
commonStockPayments           699
cashDividendsPaid            1041
netShortTermDebtIssuance     1298
commonStockDividendPaid      1351
issuanceOfCapitalStock       1717
commonStockIssuance          1765
shortTermDebtPayments        1949
shortTermDebtIssuance        1988
netPreferredStockIssuance    2702
dtype: int64

In [72]:
df[df['netIssuancePaymentsOfDebt'].isnull()].sort_values(by=['industry','company','st_date'])[finance]

company            yahoo_sector                             industry   
1667    AXON             Industrials                  Aerospace & Defense  \
1668    AXON             Industrials                  Aerospace & Defense   
1669    AXON             Industrials                  Aerospace & Defense   
3561    LULU       Consumer Cyclical                       Apparel Retail   
3558    LULU       Consumer Cyclical                       Apparel Retail   
3559    LULU       Consumer Cyclical                       Apparel Retail   
3560    LULU       Consumer Cyclical                       Apparel Retail   
3707    ROST       Consumer Cyclical                       Apparel Retail   
3761     TJX       Consumer Cyclical                       Apparel Retail   
3689      QS       Consumer Cyclical                           Auto Parts   
4092    EXEL              Healthcare                        Biotechnology   
4093    EXEL              Healthcare                        Biotechnology   
4094    EXEL              Healthcare                        Biotechnology   
4234    MRTX              Healthcare                        Biotechnology   
4235    MRTX              Healthcare                        Biotechnology   
4236    MRTX              Healthcare                        Biotechnology   
4237    MRTX              Healthcare                        Biotechnology   
4412    RARE              Healthcare                        Biotechnology   
4413    RARE              Healthcare                        Biotechnology   
4414    RARE              Healthcare                        Biotechnology   
4362    SGEN              Healthcare                        Biotechnology   
4363    SGEN              Healthcare                        Biotechnology   
4364    SGEN              Healthcare                        Biotechnology   
4360    SGEN              Healthcare                        Biotechnology   
2503    ANET              Technology                    Computer Hardware   
2506    ANET              Technology                    Computer Hardware   
2932    NTAP              Technology                    Computer Hardware   
3160    OLED              Technology                Electronic Components   
3161    OLED              Technology                Electronic Components   
3162    OLED              Technology                Electronic Components   
3158    OLED              Technology                Electronic Components   
456       EA  Communication Services       Electronic Gaming & Multimedia   
605     RBLX  Communication Services       Electronic Gaming & Multimedia   
606     RBLX  Communication Services       Electronic Gaming & Multimedia   
630     TTWO  Communication Services       Electronic Gaming & Multimedia   
631     TTWO  Communication Services       Electronic Gaming & Multimedia   
632     TTWO  Communication Services       Electronic Gaming & Multimedia   
1851    EXPD             Industrials       Integrated Freight & Logistics   
1852    EXPD             Industrials       Integrated Freight & Logistics   
596     PINS  Communication Services       Internet Content & Information   
597     PINS  Communication Services       Internet Content & Information   
598     PINS  Communication Services       Internet Content & Information   
594     PINS  Communication Services       Internet Content & Information   
3896    ALGN              Healthcare                      Medical Devices   
4046    DXCM              Healthcare                      Medical Devices   
4106    GMED              Healthcare                      Medical Devices   
4107    GMED              Healthcare                      Medical Devices   
4108    GMED              Healthcare                      Medical Devices   
4109    GMED              Healthcare                      Medical Devices   
4213    MASI              Healthcare                      Medical Devices   
4211    MASI              Healthcare                      Medical Devices   
4

In [74]:
df[df['shortTermDebtPayments'].notna()].sort_values(by=['industry','company','st_date'])[finance].head(500)

company            yahoo_sector                                industry   
1791      CW             Industrials                     Aerospace & Defense  \
1792      CW             Industrials                     Aerospace & Defense   
1793      CW             Industrials                     Aerospace & Defense   
1794      CW             Industrials                     Aerospace & Defense   
1901      GD             Industrials                     Aerospace & Defense   
1902      GD             Industrials                     Aerospace & Defense   
1903      GD             Industrials                     Aerospace & Defense   
1904      GD             Industrials                     Aerospace & Defense   
1930     HEI             Industrials                     Aerospace & Defense   
1957     HII             Industrials                     Aerospace & Defense   
1958     HII             Industrials                     Aerospace & Defense   
1959     HII             Industrials                     Aerospace & Defense   
1960     HII             Industrials                     Aerospace & Defense   
1939     HXL             Industrials                     Aerospace & Defense   
1940     HXL             Industrials                     Aerospace & Defense   
1941     HXL             Industrials                     Aerospace & Defense   
2053     LMT             Industrials                     Aerospace & Defense   
2050     LMT             Industrials                     Aerospace & Defense   
2051     LMT             Industrials                     Aerospace & Defense   
2079    MRCY             Industrials                     Aerospace & Defense   
2080    MRCY             Industrials                     Aerospace & Defense   
2081    MRCY             Industrials                     Aerospace & Defense   
2082    MRCY             Industrials                     Aerospace & Defense   
2115     NOC             Industrials                     Aerospace & Defense   
2112     NOC             Industrials                     Aerospace & Defense   
2177     RTX             Industrials                     Aerospace & Defense   
2178     RTX             Industrials                     Aerospace & Defense   
2267     SPR             Industrials                     Aerospace & Defense   
2263     SPR             Industrials                     Aerospace & Defense   
2318     TDG             Industrials                     Aerospace & Defense   
2298     TXT             Industrials                     Aerospace & Defense   
2295     TXT             Industrials                     Aerospace & Defense   
2409     WWD             Industrials                     Aerospace & Defense   
2410     WWD             Industrials                     Aerospace & Defense   
2411     WWD             Industrials                     Aerospace & Defense   
2412     WWD             Industrials                     Aerospace & Defense   
1016      CF         Basic Materials                     Agricultural Inputs   
1017      CF         Basic Materials                     Agricultural Inputs   
1013      CF         Basic Materials                     Agricultural Inputs   
1127     MOS         Basic Materials                     Agricultural Inputs   
1128     MOS         Basic Materials                     Agricultural Inputs   
1129     MOS         Basic Materials                     Agricultural Inputs   
1130     MOS         Basic Materials                     Agricultural Inputs   
1186     SMG         Basic Materials                     Agricultural Inputs   
1187     SMG         Basic Materials                     Agricultural Inputs   
1993    JBLU             Industrials                                Airlines   
1994    JBLU             Industrials                                Airlines   
1995    JBLU             Industrials                                Airlines   
2259     LUV             Industrials                                Airlines   
2260 

Take netIssuancePaymentOfDebt as net debt issued. If positive then this is net debt repaid. We can ignore the other
debt related fields.

Reasonable to set the debt related fields to 0 if null.

In [ ]:
TBD - Need to revisit this section and complete analysis

In [32]:
# Check whether issuanceOfDebt includes long and short term debt.

df[(df['shortTermDebtIssuance'] + df['longTermDebtIssuance']) != df['issuanceOfDebt']][finance].head(400)

company            yahoo_sector                               industry   
0        AM                  Energy                    Oil & Gas Midstream  \
2        AM                  Energy                    Oil & Gas Midstream   
3        AM                  Energy                    Oil & Gas Midstream   
4        AM                  Energy                    Oil & Gas Midstream   
5        AR                  Energy                          Oil & Gas E&P   
6        AR                  Energy                          Oil & Gas E&P   
7        AR                  Energy                          Oil & Gas E&P   
8        AR                  Energy                          Oil & Gas E&P   
17      BKR                  Energy         Oil & Gas Equipment & Services   
19      BKR                  Energy         Oil & Gas Equipment & Services   
20      LNG                  Energy                    Oil & Gas Midstream   
21      LNG                  Energy                    Oil & Gas Midstream   
22      LNG                  Energy                    Oil & Gas Midstream   
23      LNG                  Energy                    Oil & Gas Midstream   
34      COP                  Energy                          Oil & Gas E&P   
36      COP                  Energy                          Oil & Gas E&P   
37      COP                  Energy                          Oil & Gas E&P   
38      COP                  Energy                          Oil & Gas E&P   
39     CTRA                  Energy                          Oil & Gas E&P   
41     CTRA                  Energy                          Oil & Gas E&P   
42     CTRA                  Energy                          Oil & Gas E&P   
43     CTRA                  Energy                          Oil & Gas E&P   
44      DVN                  Energy                          Oil & Gas E&P   
45      DVN                  Energy                          Oil & Gas E&P   
46      DVN                  Energy                          Oil & Gas E&P   
47      DVN                  Energy                          Oil & Gas E&P   
49     FANG                  Energy                          Oil & Gas E&P   
56      DTM                  Energy                    Oil & Gas Midstream   
58      DTM                  Energy                    Oil & Gas Midstream   
66      EOG                  Energy                          Oil & Gas E&P   
67      EOG                  Energy                          Oil & Gas E&P   
68      EOG                  Energy                          Oil & Gas E&P   
69      EOG                  Energy                          Oil & Gas E&P   
78      XOM                  Energy                   Oil & Gas Integrated   
81      HAL                  Energy         Oil & Gas Equipment & Services   
82      HAL                  Energy         Oil & Gas Equipment & Services   
83      HAL                  Energy         Oil & Gas Equipment & Services   
84      HAL                  Energy         Oil & Gas Equipment & Services   
86      HES                  Energy                          Oil & Gas E&P   
88      HES                  Energy                          Oil & Gas E&P   
89      HES                  Energy                          Oil & Gas E&P   
90      HES                  Energy                          Oil & Gas E&P   
91     DINO                  Energy         Oil & Gas Refining & Marketing   
93     DINO                  Energy         Oil & Gas Refining & Marketing   
94     DINO                  Energy         Oil & Gas Refining & Marketing   
95     DINO                  Energy         Oil & Gas Refining & Marketing   
96      KMI                  Energy                    Oil & Gas Midstream   
98      KMI                  Energy                    Oil & Gas Midstream   
99      KMI                  Energy                    Oil & Gas Midstream   
100     KMI                  Energy                    Oil & Gas Midstream   
101     MRO               

Conclusion: issuanceOfDebt is longTermDebtIssuance only.

In [ ]:
df[(df['shortTermDebtIssuance'] + df['longTermDebtIssuance']) != df['issuanceOfDebt']][finance]

In [37]:
# Check that netIssuancePaymentsOfDebt is equal to the sum of short and long term debt.

col_list = ['company','st_date','netShortTermDebtIssuance','netLongTermDebtIssuance','netIssuancePaymentsOfDebt']
df[(df['netShortTermDebtIssuance'] + df['netLongTermDebtIssuance']) != df['netIssuancePaymentsOfDebt']][col_list].head(500)

company     st_date  netShortTermDebtIssuance  netLongTermDebtIssuance   
5         AR  2019-12-31                       NaN             690908000.00  \
6         AR  2020-12-31                       NaN            -466519000.00   
12       APA  2019-12-31              396000000.00             235000000.00   
15       BKR  2022-12-31              -28000000.00             -28000000.00   
17       BKR  2019-12-31             -542000000.00            -587000000.00   
20       LNG  2019-12-31                       NaN            2088000000.00   
21       LNG  2020-12-31                       NaN             883000000.00   
22       LNG  2021-12-31                       NaN            -899000000.00   
23       LNG  2022-12-31                       NaN           -5203000000.00   
29       CVX  2022-12-31              263000000.00           -8742000000.00   
30       CVX  2019-12-31            -2821000000.00           -7800000000.00   
31       CVX  2020-12-31              651000000.00            7500000000.00   
32       CVX  2021-12-31            -5572000000.00          -12900000000.00   
34       COP  2022-12-31                       NaN           -3370000000.00   
36       COP  2019-12-31                       NaN             -80000000.00   
37       COP  2020-12-31                       NaN              46000000.00   
38       COP  2021-12-31                       NaN            -505000000.00   
39      CTRA  2022-12-31                       NaN            -880000000.00   
41      CTRA  2019-12-31                       NaN              -7000000.00   
42      CTRA  2020-12-31                       NaN             -87000000.00   
43      CTRA  2021-12-31                       NaN            -190000000.00   
44       DVN  2019-12-31                       NaN            -162000000.00   
45       DVN  2020-12-31                       NaN                     0.00   
46       DVN  2021-12-31                       NaN           -1243000000.00   
47       DVN  2022-12-31                       NaN                     0.00   
56       DTM  2020-12-31              253000000.00                      NaN   
66       EOG  2019-12-31                       NaN            -912899000.00   
67       EOG  2020-12-31                       NaN             464408000.00   
68       EOG  2021-12-31                       NaN            -787000000.00   
69       EOG  2022-12-31                       NaN             -10000000.00   
81       HAL  2019-12-31                       NaN             -13000000.00   
82       HAL  2020-12-31                       NaN            -660000000.00   
83       HAL  2021-12-31                       NaN            -700000000.00   
84       HAL  2022-12-31                       NaN           -1242000000.00   
91      DINO  2022-12-31                       NaN             174867000.00   
93      DINO  2019-12-31               42500000.00              40949000.00   
94      DINO  2020-12-31              -52000000.00             671430000.00   
95      DINO  2021-12-31              -73500000.00             -77490000.00   
96       KMI  2022-12-31                       NaN            -677000000.00   
98       KMI  2019-12-31                       NaN           -3188000000.00   
99       KMI  2020-12-31                       NaN            -108000000.00   
100      KMI  2021-12-31                       NaN            -872000000.00   
101      MRO  2022-12-31                       NaN            1915000000.00   
103      MRO  2019-12-31                       NaN                     0.00   
104      MRO  2020-12-31                       NaN            -100000000.00   
105      MRO  2021-12-31                       NaN           -1400000000.00   
111      NFE  2022-12-31                       NaN             511207000.00   
113      NFE  2019-12-31                       NaN             342856000.00   
114      NFE  2021-12-31                       NaN            1973635000.00   
116      NFE  2020-12-31                       NaN     

Didn't expect this. Totally inconsistent whether netIssuancePaymentsOfDebt includes long and short term. Disregard
this field as it is unreliable.

In [40]:
# Let's check that netShortTermDebtIssuance is equal to sum of shortTermIssuance and shortTermPayments

df[(df['shortTermDebtIssuance'] + df['shortTermDebtPayments']) != df['netShortTermDebtIssuance']][finance].head(500)

company            yahoo_sector                               industry   
0        AM                  Energy                    Oil & Gas Midstream  \
2        AM                  Energy                    Oil & Gas Midstream   
3        AM                  Energy                    Oil & Gas Midstream   
4        AM                  Energy                    Oil & Gas Midstream   
5        AR                  Energy                          Oil & Gas E&P   
6        AR                  Energy                          Oil & Gas E&P   
7        AR                  Energy                          Oil & Gas E&P   
8        AR                  Energy                          Oil & Gas E&P   
10      APA                  Energy                          Oil & Gas E&P   
12      APA                  Energy                          Oil & Gas E&P   
13      APA                  Energy                          Oil & Gas E&P   
14      APA                  Energy                          Oil & Gas E&P   
15      BKR                  Energy         Oil & Gas Equipment & Services   
17      BKR                  Energy         Oil & Gas Equipment & Services   
18      BKR                  Energy         Oil & Gas Equipment & Services   
19      BKR                  Energy         Oil & Gas Equipment & Services   
20      LNG                  Energy                    Oil & Gas Midstream   
21      LNG                  Energy                    Oil & Gas Midstream   
22      LNG                  Energy                    Oil & Gas Midstream   
23      LNG                  Energy                    Oil & Gas Midstream   
34      COP                  Energy                          Oil & Gas E&P   
36      COP                  Energy                          Oil & Gas E&P   
37      COP                  Energy                          Oil & Gas E&P   
38      COP                  Energy                          Oil & Gas E&P   
39     CTRA                  Energy                          Oil & Gas E&P   
41     CTRA                  Energy                          Oil & Gas E&P   
42     CTRA                  Energy                          Oil & Gas E&P   
43     CTRA                  Energy                          Oil & Gas E&P   
44      DVN                  Energy                          Oil & Gas E&P   
45      DVN                  Energy                          Oil & Gas E&P   
46      DVN                  Energy                          Oil & Gas E&P   
47      DVN                  Energy                          Oil & Gas E&P   
56      DTM                  Energy                    Oil & Gas Midstream   
58      DTM                  Energy                    Oil & Gas Midstream   
66      EOG                  Energy                          Oil & Gas E&P   
67      EOG                  Energy                          Oil & Gas E&P   
68      EOG                  Energy                          Oil & Gas E&P   
69      EOG                  Energy                          Oil & Gas E&P   
78      XOM                  Energy                   Oil & Gas Integrated   
81      HAL                  Energy         Oil & Gas Equipment & Services   
82      HAL                  Energy         Oil & Gas Equipment & Services   
83      HAL                  Energy         Oil & Gas Equipment & Services   
84      HAL                  Energy         Oil & Gas Equipment & Services   
86      HES                  Energy                          Oil & Gas E&P   
88      HES                  Energy                          Oil & Gas E&P   
89      HES                  Energy                          Oil & Gas E&P   
90      HES                  Energy                          Oil & Gas E&P   
91     DINO                  Energy         Oil & Gas Refining & Marketing   
96      KMI                  Energy                    Oil & Gas Midstream   
98      KMI                  Energy                    Oil & Gas Midstream   
99      KMI               

Plenty of inconsistencies. Many cases where netShortTermDebtIssuance is populated but the other two fields aren't.
The totals do not always add up. 
Best we can do is take netShortTermDebtIssuance in the final cut as representative of net ShortTermDebt.


In [41]:
# Let's check that netLongTermDebtIssuance is equal to sum of longTermIssuance and longTermPayments

df[(df['longTermDebtIssuance'] + df['longTermDebtPayments']) != df['netLongTermDebtIssuance']][finance].head(500)

company            yahoo_sector                               industry   
2         AM                  Energy                    Oil & Gas Midstream  \
3         AM                  Energy                    Oil & Gas Midstream   
12       APA                  Energy                          Oil & Gas E&P   
13       APA                  Energy                          Oil & Gas E&P   
17       BKR                  Energy         Oil & Gas Equipment & Services   
30       CVX                  Energy                   Oil & Gas Integrated   
31       CVX                  Energy                   Oil & Gas Integrated   
32       CVX                  Energy                   Oil & Gas Integrated   
36       COP                  Energy                          Oil & Gas E&P   
39      CTRA                  Energy                          Oil & Gas E&P   
41      CTRA                  Energy                          Oil & Gas E&P   
43      CTRA                  Energy                          Oil & Gas E&P   
44       DVN                  Energy                          Oil & Gas E&P   
45       DVN                  Energy                          Oil & Gas E&P   
46       DVN                  Energy                          Oil & Gas E&P   
47       DVN                  Energy                          Oil & Gas E&P   
49      FANG                  Energy                          Oil & Gas E&P   
56       DTM                  Energy                    Oil & Gas Midstream   
66       EOG                  Energy                          Oil & Gas E&P   
69       EOG                  Energy                          Oil & Gas E&P   
81       HAL                  Energy         Oil & Gas Equipment & Services   
120      NOV                  Energy         Oil & Gas Equipment & Services   
121      NOV                  Energy         Oil & Gas Equipment & Services   
135      OVV                  Energy                          Oil & Gas E&P   
152      PXD                  Energy                          Oil & Gas E&P   
165      SWN                  Energy                          Oil & Gas E&P   
166      SWN                  Energy                          Oil & Gas E&P   
175      TPL                  Energy                          Oil & Gas E&P   
177      TPL                  Energy                          Oil & Gas E&P   
178      TPL                  Energy                          Oil & Gas E&P   
179      TPL                  Energy                          Oil & Gas E&P   
339      NRG               Utilities  Utilities—Independent Power Producers   
340      NRG               Utilities  Utilities—Independent Power Producers   
341      NRG               Utilities  Utilities—Independent Power Producers   
390      VST               Utilities  Utilities—Independent Power Producers   
456       EA  Communication Services         Electronic Gaming & Multimedia   
468      FOX  Communication Services                          Entertainment   
469      FOX  Communication Services                          Entertainment   
470      FOX  Communication Services                          Entertainment   
537     MSGS  Communication Services                          Entertainment   
538     MSGS  Communication Services                          Entertainment   
548     META  Communication Services         Internet Content & Information   
549     META  Communication Services         Internet Content & Information   
550     META  Communication Services         Internet Content & Information   
553     NFLX  Communication Services                          Entertainment   
554     NFLX  Communication Services                          Entertainment   
556      NYT  Communication Services                             Publishing   
558      NYT  Communication Services                             Publishing   
559      NYT  Communication Services                             Publishing   
560      NYT  Communication Services                   

Similar inconsistencies as with shortTermDebt. Make a decision to just use netLongTermDebtIssuance.

In [42]:
# Check the following.

df[(df['issuanceOfDebt'] + df['repaymentOfDebt']) != df['netIssuancePaymentsOfDebt']][finance].head(500)

company            yahoo_sector                             industry   
0         AM                  Energy                  Oil & Gas Midstream  \
7         AR                  Energy                        Oil & Gas E&P   
8         AR                  Energy                        Oil & Gas E&P   
13       APA                  Energy                        Oil & Gas E&P   
17       BKR                  Energy       Oil & Gas Equipment & Services   
19       BKR                  Energy       Oil & Gas Equipment & Services   
29       CVX                  Energy                 Oil & Gas Integrated   
30       CVX                  Energy                 Oil & Gas Integrated   
31       CVX                  Energy                 Oil & Gas Integrated   
32       CVX                  Energy                 Oil & Gas Integrated   
36       COP                  Energy                        Oil & Gas E&P   
39      CTRA                  Energy                        Oil & Gas E&P   
41      CTRA                  Energy                        Oil & Gas E&P   
43      CTRA                  Energy                        Oil & Gas E&P   
44       DVN                  Energy                        Oil & Gas E&P   
45       DVN                  Energy                        Oil & Gas E&P   
46       DVN                  Energy                        Oil & Gas E&P   
47       DVN                  Energy                        Oil & Gas E&P   
56       DTM                  Energy                  Oil & Gas Midstream   
66       EOG                  Energy                        Oil & Gas E&P   
69       EOG                  Energy                        Oil & Gas E&P   
81       HAL                  Energy       Oil & Gas Equipment & Services   
86       HES                  Energy                        Oil & Gas E&P   
88       HES                  Energy                        Oil & Gas E&P   
89       HES                  Energy                        Oil & Gas E&P   
90       HES                  Energy                        Oil & Gas E&P   
121      NOV                  Energy       Oil & Gas Equipment & Services   
123      OXY                  Energy                        Oil & Gas E&P   
128      OKE                  Energy                  Oil & Gas Midstream   
129      OKE                  Energy                  Oil & Gas Midstream   
135      OVV                  Energy                        Oil & Gas E&P   
152      PXD                  Energy                        Oil & Gas E&P   
160      SLB                  Energy       Oil & Gas Equipment & Services   
161      SLB                  Energy       Oil & Gas Equipment & Services   
162      SLB                  Energy       Oil & Gas Equipment & Services   
163      SLB                  Energy       Oil & Gas Equipment & Services   
175      TPL                  Energy                        Oil & Gas E&P   
177      TPL                  Energy                        Oil & Gas E&P   
178      TPL                  Energy                        Oil & Gas E&P   
179      TPL                  Energy                        Oil & Gas E&P   
189      WMB                  Energy                  Oil & Gas Midstream   
192      WMB                  Energy                  Oil & Gas Midstream   
200      LNT               Utilities         Utilities—Regulated Electric   
202      LNT               Utilities         Utilities—Regulated Electric   
203      LNT               Utilities         Utilities—Regulated Electric   
204      LNT               Utilities         Utilities—Regulated Electric   
205      AEE               Utilities         Utilities—Regulated Electric   
207      AEE               Utilities         Utilities—Regulated Electric   
208      AEE               Utilities         Utilities—Regulated Electric   
209      AEE               Utilities         Utilities—Regulated Electric   
215      AWK               Utilities            Utilities—Regulated Water   
2

Plenty of discrepenacies. Take netIssuancePaymentsOfDebt, netShortTermDebtIssuance and netLongTermDebtIssuance 
in final cut and accept as reported. 

In [50]:
# Check for the case where both related fields are null but netCommonStockIssuance isn't.

df[df['issuanceOfDebt'].isnull() & \
   df['repaymentOfDebt'].isnull() & \
   df['netIssuancePaymentsOfDebt'].notna()][finance].head(400)

company        yahoo_sector                                industry   
848     MNST  Consumer Defensive                 Beverages—Non-Alcoholic  \
852     MNST  Consumer Defensive                 Beverages—Non-Alcoholic   
1724    CARR         Industrials           Building Products & Equipment   
1817     DOV         Industrials          Specialty Industrial Machinery   
2048    LECO         Industrials                     Tools & Accessories   
2135    OTIS         Industrials          Specialty Industrial Machinery   
2249     AOS         Industrials          Specialty Industrial Machinery   
2250     AOS         Industrials          Specialty Industrial Machinery   
2427     ACN          Technology         Information Technology Services   
2428     ACN          Technology         Information Technology Services   
2429     ACN          Technology         Information Technology Services   
2430     ACN          Technology         Information Technology Services   
3004    PCOR          Technology                    Software—Application   
3006    PCOR          Technology                    Software—Application   
3007    PCOR          Technology                    Software—Application   
3137     TYL          Technology                    Software—Application   
3181     VNT          Technology      Scientific & Technical Instruments   
4241    MRNA          Healthcare                           Biotechnology   
4465     ZTS          Healthcare  Drug Manufacturers—Specialty & Generic   

         st_date  shortTermDebtIssuance  shortTermDebtPayments   
848   2022-12-31                    NaN                    NaN  \
852   2021-12-31                    NaN                    NaN   
1724  2019-12-31                    NaN                    NaN   
1817  2022-12-31                    NaN                    NaN   
2048  2021-12-31                    NaN                    NaN   
2135  2019-12-31                    NaN                    NaN   
2249  2019-12-31                    NaN                    NaN   
2250  2020-12-31                    NaN                    NaN   
2427  2019-08-31                    NaN                    NaN   
2428  2020-08-31                    NaN                    NaN   
2429  2021-08-31                    NaN                    NaN   
2430  2022-08-31                    NaN                    NaN   
3004  2022-12-31                    NaN                    NaN   
3006  2019-12-31                    NaN                    NaN   
3007  2020-12-31                    NaN                    NaN   
3137  2019-12-31                    NaN                    NaN   
3181  2019-12-31                    NaN                    NaN   
4241  2022-12-31                    NaN                    NaN   
4465  2019-12-31                    NaN                    NaN   

      netShortTermDebtIssuance  longTermDebtIssuance  longTermDebtPayments   
848                        NaN                   NaN                   NaN  \
852                        NaN                   NaN                   NaN   
1724               25000000.00                   NaN                   NaN   
1817              629891000.00                   NaN                   NaN   
2048                       NaN                   NaN                   NaN   
2135                6000000.00                   NaN                   NaN   
2249                       NaN                   NaN                   NaN   
2250                       NaN                   NaN                   NaN   
2427                       NaN                   NaN                   NaN   
2428                       NaN                   NaN                   NaN   
2429                       NaN                   NaN                   NaN   
2430                       NaN                   NaN                   NaN   
3004                       NaN                   NaN                   NaN   
3006                       NaN                   NaN                   

In [52]:
df[(df['issuanceOfDebt'].notna() |\
   df['repaymentOfDebt'].notna()) & \
   df['netIssuancePaymentsOfDebt'].isnull()][finance].head(400)

Empty DataFrame
Columns: [company, yahoo_sector, industry, st_date, shortTermDebtIssuance, shortTermDebtPayments, netShortTermDebtIssuance, longTermDebtIssuance, longTermDebtPayments, netLongTermDebtIssuance, issuanceOfDebt, repaymentOfDebt, netIssuancePaymentsOfDebt, commonStockDividendPaid, commonStockIssuance, commonStockPayments, netCommonStockIssuance, issuanceOfCapitalStock, netPreferredStockIssuance, commonStockDividendPaid, netOtherFinancingCharges, repurchaseOfCapitalStock]
Index: []

In [48]:
# Check for the case where both related fields are null but netCommonStockIssuance isn't.

df[df['commonStockIssuance'].isnull() & \
   df['commonStockPayments'].isnull() & \
   df['netCommonStockIssuance'].notna()][finance].head(400)


company        yahoo_sector                        industry     st_date   
32       CVX              Energy            Oil & Gas Integrated  2021-12-31  \
324      NFG              Energy            Oil & Gas Integrated  2019-09-30   
325      NFG              Energy            Oil & Gas Integrated  2020-09-30   
326      NFG              Energy            Oil & Gas Integrated  2021-09-30   
354      PNW           Utilities    Utilities—Regulated Electric  2022-12-31   
356      PNW           Utilities    Utilities—Regulated Electric  2019-12-31   
357      PNW           Utilities    Utilities—Regulated Electric  2020-12-31   
358      PNW           Utilities    Utilities—Regulated Electric  2021-12-31   
800     INGR  Consumer Defensive                  Packaged Foods  2021-12-31   
1893      GE         Industrials  Specialty Industrial Machinery  2019-12-31   
2416     XPO         Industrials                        Trucking  2021-12-31   

      shortTermDebtIssuance  shortTermDebtPayments  netShortTermDebtIssuance   
32            4448000000.00        -10020000000.00            -5572000000.00  \
324                     NaN                    NaN               55200000.00   
325                     NaN                    NaN              -25200000.00   
326                     NaN                    NaN              128500000.00   
354             48720000.00                   0.00               48720000.00   
356            103275000.00           -65000000.00               38275000.00   
357            825015000.00          -770690000.00               54325000.00   
358            142000000.00           -19000000.00              123000000.00   
800                     NaN                    NaN              250000000.00   
1893                    NaN                    NaN              280000000.00   
2416                   0.00          -200000000.00                      0.00   

      longTermDebtIssuance  longTermDebtPayments  netLongTermDebtIssuance   
32                    0.00        -7364000000.00          -12900000000.00  \
324                   0.00                  0.00                     0.00   
325           493007000.00                  0.00             493007000.00   
326           495267000.00         -515715000.00             -20448000.00   
354           875537000.00         -150000000.00             725537000.00   
356          1092188000.00         -600000000.00             492188000.00   
357          1596672000.00         -915150000.00             681522000.00   
358           746999000.00                  0.00             746999000.00   
800          1300000000.00        -1690000000.00            -390000000.00   
1893         2185000000.00       -16567000000.00          -14382000000.00   
2416                  0.00        -3073000000.00           -3073000000.00   

      issuanceOfDebt  repaymentOfDebt  netIssuancePaymentsOfDebt   
32     4448000000.00  -17384000000.00            -12900000000.00  \
324             0.00             0.00                55200000.00   
325     493007000.00             0.00               467807000.00   
326     495267000.00    -515715000.00               108052000.00   
354     924257000.00    -150000000.00               774257000.00   
356    1195463000.00    -665000000.00               530463000.00   
357    2421687000.00   -1685840000.00               735847000.00   
358     888999000.00     -19000000.00               869999000.00   
800    1300000000.00   -1690000000.00              -140000000.00   
1893   2185000000.00  -16567000000.00            -14102000000.00   
2416            0.00   -3073000000.00             -3073000000.00   

      commonStockDividendPaid  commonStockIssuance  commonStockPayments   
32            -10200000000.00                  NaN                  NaN  \
324             -147418000.00                  NaN                  NaN   
325             -153322000.00                  NaN                  NaN   
326             -163089000.00            

In [49]:
# Check for case where netCommonStockIssuance is null but related fields aren't

df[(df['commonStockIssuance'].notna() | \
   df['commonStockPayments'].notna()) & \
   df['netCommonStockIssuance'].isnull()][finance].head(400)

Empty DataFrame
Columns: [company, yahoo_sector, industry, st_date, shortTermDebtIssuance, shortTermDebtPayments, netShortTermDebtIssuance, longTermDebtIssuance, longTermDebtPayments, netLongTermDebtIssuance, issuanceOfDebt, repaymentOfDebt, netIssuancePaymentsOfDebt, commonStockDividendPaid, commonStockIssuance, commonStockPayments, netCommonStockIssuance, issuanceOfCapitalStock, netPreferredStockIssuance, commonStockDividendPaid, netOtherFinancingCharges, repurchaseOfCapitalStock]
Index: []

Conclusion: netCommonStockIssuance is the most reliable field for stock issued and should be included in final cut
as stock issued.

In [73]:
# cashDividendsPaid has a lower null count than commonStockDividendPaid. Check if there are cases where 
# cashDividendsPaid is null but commonStockDividendPaid is populated.

df[df['cashDividendsPaid'].isnull() & df['commonStockDividendPaid'].notna()][finance]

Empty DataFrame
Columns: [company, yahoo_sector, industry, st_date, shortTermDebtIssuance, shortTermDebtPayments, netShortTermDebtIssuance, longTermDebtIssuance, longTermDebtPayments, netLongTermDebtIssuance, issuanceOfDebt, repaymentOfDebt, netIssuancePaymentsOfDebt, cashDividendsPaid, commonStockDividendPaid, commonStockIssuance, commonStockPayments, netCommonStockIssuance, issuanceOfCapitalStock, netPreferredStockIssuance, netOtherFinancingCharges, repurchaseOfCapitalStock]
Index: []

In [83]:
# Sanity check to confirm that cashDividends paid is the sum of dividends paid for common and preferred shares.

df_temp = df[['company','st_date','cashDividendsPaid',
             'commonStockDividendPaid','preferredStockDividendPaid']].copy()
df_temp['totalDividendsPaid'] = df_temp['commonStockDividendPaid'] + df_temp['preferredStockDividendPaid']

df_temp[df_temp['cashDividendsPaid'].notna()].head(300)

company     st_date  cashDividendsPaid  commonStockDividendPaid   
0        AM  2022-12-31      -433375000.00            -432825000.00  \
2        AM  2019-12-31      -496197000.00            -495823000.00   
3        AM  2020-12-31      -590190000.00            -589640000.00   
4        AM  2021-12-31      -471721000.00            -471171000.00   
10      APA  2022-12-31      -218000000.00            -207000000.00   
12      APA  2019-12-31      -376000000.00            -376000000.00   
13      APA  2020-12-31      -146000000.00            -123000000.00   
14      APA  2021-12-31       -98000000.00             -52000000.00   
15      BKR  2022-12-31      -743000000.00            -743000000.00   
17      BKR  2019-12-31      -745000000.00            -745000000.00   
18      BKR  2020-12-31      -744000000.00            -744000000.00   
19      BKR  2021-12-31      -749000000.00                      NaN   
22      LNG  2021-12-31       -85000000.00             -85000000.00   
23      LNG  2022-12-31      -349000000.00            -349000000.00   
29      CVX  2022-12-31    -10968000000.00          -11000000000.00   
30      CVX  2019-12-31     -9000000000.00           -9000000000.00   
31      CVX  2020-12-31     -9700000000.00           -9700000000.00   
32      CVX  2021-12-31    -10200000000.00          -10200000000.00   
34      COP  2022-12-31     -5726000000.00           -5726000000.00   
36      COP  2019-12-31     -1500000000.00           -1500000000.00   
37      COP  2020-12-31     -1831000000.00           -1831000000.00   
38      COP  2021-12-31     -2359000000.00           -2359000000.00   
39     CTRA  2022-12-31     -1992000000.00           -1992000000.00   
41     CTRA  2019-12-31      -145515000.00            -145515000.00   
42     CTRA  2020-12-31      -159390000.00            -159390000.00   
43     CTRA  2021-12-31      -780000000.00            -780000000.00   
44      DVN  2019-12-31      -140000000.00            -140000000.00   
45      DVN  2020-12-31      -257000000.00            -257000000.00   
46      DVN  2021-12-31     -1315000000.00           -1315000000.00   
47      DVN  2022-12-31     -3379000000.00           -3379000000.00   
49     FANG  2022-12-31     -1572000000.00           -1572000000.00   
51     FANG  2019-12-31      -112000000.00            -112000000.00   
52     FANG  2020-12-31      -236000000.00            -236000000.00   
53     FANG  2021-12-31      -312000000.00            -312000000.00   
55      DTM  2019-12-31               0.00                     0.00   
57      DTM  2021-12-31      -559000000.00            -559000000.00   
58      DTM  2022-12-31      -244000000.00            -244000000.00   
61      EVA  2022-12-31      -211061000.00                      NaN   
63      EVA  2019-12-31       -95659000.00             -95659000.00   
64      EVA  2020-12-31      -133217000.00            -133217000.00   
65      EVA  2021-12-31      -116006000.00                      NaN   
66      EOG  2019-12-31      -588200000.00            -588200000.00   
67      EOG  2020-12-31      -820823000.00            -820823000.00   
68      EOG  2021-12-31     -2684000000.00           -2684000000.00   
69      EOG  2022-12-31     -5148000000.00           -5148000000.00   
71      EQT  2019-12-31       -30655000.00             -30655000.00   
72      EQT  2020-12-31        -7664000.00              -7664000.00   
73      EQT  2021-12-31               0.00                      NaN   
74      EQT  2022-12-31      -203629000.00            -203629000.00   
76      XOM  2022-12-31    -14939000000.00          -14939000000.00   
77      XOM  2019-12-31    -14652000000.00          -14652000000.00   
78      XOM  2020-12-31    -14865000000.00          -14865000000.00   
79      XOM  2021-12-31    -14924000000.00          -14924000000.00   
81      HAL  2019-12-31      -630000000.00            -630000000.00   
82      HAL  2020-12-31      -278000000.00            -278000000.00   
83      HAL  2021-12-31     

In [88]:
# Set selected fields to 0 if not popupated

col_list = ['netIssuancePaymentsOfDebt','netLongTermDebtIssuance','netShortTermDebtIssuance',
            'commonStockDividendPaid', 'netCommonStockIssuance', 'netOtherFinancingCharges',
            'cashDividendsPaid']

df[col_list] = df[col_list].fillna(0)

In [86]:
# Check null counts

df[finance].isnull().sum().sort_values()

company                          0
yahoo_sector                     0
industry                         0
st_date                          0
netCommonStockIssuance           0
commonStockDividendPaid          0
netShortTermDebtIssuance         0
cashDividendsPaid                0
netIssuancePaymentsOfDebt        0
netLongTermDebtIssuance          0
netOtherFinancingCharges         0
repaymentOfDebt                188
longTermDebtPayments           257
issuanceOfDebt                 290
longTermDebtIssuance           394
repurchaseOfCapitalStock       667
commonStockPayments            699
issuanceOfCapitalStock        1717
commonStockIssuance           1765
shortTermDebtPayments         1949
shortTermDebtIssuance         1988
netPreferredStockIssuance     2702
preferredStockDividendPaid    2846
dtype: int64

In [102]:
final_finance = ['netCommonStockIssuance','cashDividendsPaid','netIssuancePaymentsOfDebt',
                 'netLongTermDebtIssuance','netShortTermDebtIssuance','netOtherFinancingCharges',
                 'repurchaseOfCapitalStock', 'cashFlowFromContinuingFinancingActivities']

is_col_name_mapping['cf_financeCashFlow'] = 'cashFlowFromContinuingFinanceActivities'

## Adhoc

In [76]:
df[adhoc].isnull().sum().sort_values()

company                                      0
yahoo_sector                                 0
industry                                     0
st_date                                      0
cashFlowFromContinuingOperatingActivities    0
capitalExpenditure                           0
freeCashFlow                                 0
dtype: int64

In [78]:
df[adhoc].sort_values(by=['industry','company','st_date']).head(500)

company            yahoo_sector                           industry   
484      IPG  Communication Services               Advertising Agencies  \
485      IPG  Communication Services               Advertising Agencies   
486      IPG  Communication Services               Advertising Agencies   
487      IPG  Communication Services               Advertising Agencies   
579      OMC  Communication Services               Advertising Agencies   
580      OMC  Communication Services               Advertising Agencies   
581      OMC  Communication Services               Advertising Agencies   
582      OMC  Communication Services               Advertising Agencies   
1667    AXON             Industrials                Aerospace & Defense   
1668    AXON             Industrials                Aerospace & Defense   
1669    AXON             Industrials                Aerospace & Defense   
1670    AXON             Industrials                Aerospace & Defense   
1681      BA             Industrials                Aerospace & Defense   
1682      BA             Industrials                Aerospace & Defense   
1683      BA             Industrials                Aerospace & Defense   
1679      BA             Industrials                Aerospace & Defense   
1700    BWXT             Industrials                Aerospace & Defense   
1701    BWXT             Industrials                Aerospace & Defense   
1702    BWXT             Industrials                Aerospace & Defense   
1703    BWXT             Industrials                Aerospace & Defense   
1791      CW             Industrials                Aerospace & Defense   
1792      CW             Industrials                Aerospace & Defense   
1793      CW             Industrials                Aerospace & Defense   
1794      CW             Industrials                Aerospace & Defense   
1901      GD             Industrials                Aerospace & Defense   
1902      GD             Industrials                Aerospace & Defense   
1903      GD             Industrials                Aerospace & Defense   
1904      GD             Industrials                Aerospace & Defense   
1928     HEI             Industrials                Aerospace & Defense   
1929     HEI             Industrials                Aerospace & Defense   
1930     HEI             Industrials                Aerospace & Defense   
1931     HEI             Industrials                Aerospace & Defense   
1957     HII             Industrials                Aerospace & Defense   
1958     HII             Industrials                Aerospace & Defense   
1959     HII             Industrials                Aerospace & Defense   
1960     HII             Industrials                Aerospace & Defense   
1949     HWM             Industrials                Aerospace & Defense   
1950     HWM             Industrials                Aerospace & Defense   
1951     HWM             Industrials                Aerospace & Defense   
1947     HWM             Industrials                Aerospace & Defense   
1939     HXL             Industrials                Aerospace & Defense   
1940     HXL             Industrials                Aerospace & Defense   
1941     HXL             Industrials                Aerospace & Defense   
1937     HXL             Industrials                Aerospace & Defense   
2025     LHX             Industrials                Aerospace & Defense   
2026     LHX             Industrials                Aerospace & Defense   
2027     LHX             Industrials                Aerospace & Defense   
2022     LHX             Industrials                Aerospace & Defense   
2053     LMT             Industrials                Aerospace & Defense   
2050     LMT             Industrials                Aerospace & Defense   
2051     LMT             Industrials                Aerospace & Defense   
2049     LMT             Industrials                Aerospace & Defense   
2079    MRCY             Indus

In [97]:
final_adhoc = ['freeCashFlow']

## Save Modified Data

In [89]:
with open('/home/priyesh/projects/TS1/pickle/yahoo_modified_cash_sheets.pkl','wb') as f:
    pickle.dump(df,f)

In [90]:
with open('/home/priyesh/projects/TS1/pickle/yahoo_drop_data_details_stage5.pkl','wb') as f:
    pickle.dump(drop_data_details,f)

## Build final cut data for cash sheet

In [3]:
df = df.reset_index(drop=True)

NameError: name 'df' is not defined

In [103]:
col_list = ['company', 'yahoo_sector','gics_sector','industry','st_date', 'st_YR','st_Mnth'] + \
           final_operating + final_investing + final_finance + final_adhoc

df_final = df[col_list].copy()

In [105]:
df_final.head(100)

company     yahoo_sector gics_sector                        industry   
0        AM           Energy      Energy             Oil & Gas Midstream  \
2        AM           Energy      Energy             Oil & Gas Midstream   
3        AM           Energy      Energy             Oil & Gas Midstream   
4        AM           Energy      Energy             Oil & Gas Midstream   
5        AR           Energy      Energy                   Oil & Gas E&P   
6        AR           Energy      Energy                   Oil & Gas E&P   
7        AR           Energy      Energy                   Oil & Gas E&P   
8        AR           Energy      Energy                   Oil & Gas E&P   
10      APA           Energy      Energy                   Oil & Gas E&P   
12      APA           Energy      Energy                   Oil & Gas E&P   
13      APA           Energy      Energy                   Oil & Gas E&P   
14      APA           Energy      Energy                   Oil & Gas E&P   
15      BKR           Energy      Energy  Oil & Gas Equipment & Services   
17      BKR           Energy      Energy  Oil & Gas Equipment & Services   
18      BKR           Energy      Energy  Oil & Gas Equipment & Services   
19      BKR           Energy      Energy  Oil & Gas Equipment & Services   
20      LNG           Energy      Energy             Oil & Gas Midstream   
21      LNG           Energy      Energy             Oil & Gas Midstream   
22      LNG           Energy      Energy             Oil & Gas Midstream   
23      LNG           Energy      Energy             Oil & Gas Midstream   
29      CVX           Energy      Energy            Oil & Gas Integrated   
30      CVX           Energy      Energy            Oil & Gas Integrated   
31      CVX           Energy      Energy            Oil & Gas Integrated   
32      CVX           Energy      Energy            Oil & Gas Integrated   
34      COP           Energy      Energy                   Oil & Gas E&P   
36      COP           Energy      Energy                   Oil & Gas E&P   
37      COP           Energy      Energy                   Oil & Gas E&P   
38      COP           Energy      Energy                   Oil & Gas E&P   
39     CTRA           Energy      Energy                   Oil & Gas E&P   
41     CTRA           Energy      Energy                   Oil & Gas E&P   
42     CTRA           Energy      Energy                   Oil & Gas E&P   
43     CTRA           Energy      Energy                   Oil & Gas E&P   
44      DVN           Energy      Energy                   Oil & Gas E&P   
45      DVN           Energy      Energy                   Oil & Gas E&P   
46      DVN           Energy      Energy                   Oil & Gas E&P   
47      DVN           Energy      Energy                   Oil & Gas E&P   
49     FANG           Energy      Energy                   Oil & Gas E&P   
51     FANG           Energy      Energy                   Oil & Gas E&P   
52     FANG           Energy      Energy                   Oil & Gas E&P   
53     FANG           Energy      Energy                   Oil & Gas E&P   
55      DTM           Energy      Energy             Oil & Gas Midstream   
56      DTM           Energy      Energy             Oil & Gas Midstream   
57      DTM           Energy      Energy             Oil & Gas Midstream   
58      DTM           Energy      Energy             Oil & Gas Midstream   
61      EVA  Basic Materials      Energy        Lumber & Wood Production   
63      EVA  Basic Materials      Energy        Lumber & Wood Production   
64      EVA  Basic Materials      Energy        Lumber & Wood Production   
65      EVA  Basic Materials      Energy        Lumber & Wood Production   
66      EOG           Energy      Energy                   Oil & Gas E&P   
67      EOG           Energy      Energy                   Oil & Gas E&P   
68      EOG           Energy      Energy                   Oil & Gas E&P   
69      EOG           Energy      Energy            

In [106]:
# Save final cut

with open('/home/priyesh/projects/TS1/pickle/yahoo_cash_sheets_final_stage5.pkl','wb') as f:
    pickle.dump(df_final,f)